In [1]:
import pandas as pd
import os
import base64
import time
import pickle as p
import numpy as np
import matplotlib.pyplot as plt
import pandas.core.algorithms as algos
from sklearn.model_selection import train_test_split
from sklearn import metrics

import logging
import matplotlib.style as style
import matplotlib
import matplotlib.lines as mlines
from matplotlib.ticker import FuncFormatter
style.use('seaborn')

import warnings
warnings.filterwarnings('ignore')

In [2]:
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)

In [3]:
import gc
gc.collect()

97

In [ ]:
Client = pd.read_excel('./data/Client_info_20191118.xlsx',sheet_name='Sheet1')
TPA = pd.read_excel('./data/Copy_of_TPA_cash.xlsx',sheet_name='Sheet1')
Client = Client.merge(TPA,how='left',left_on='Client ID',right_on='HOST ID')
Customer = pd.read_csv('./data/Customer_Data_Request_20191121.csv')

In [52]:
Client.head()

Active  Client ID                    Account Name  Current Eligibles  Eligibles at time of Launch                                       Industry  NAICS Code                                  NAICS Description                               Broker TPA_x Launch Date Termination Date Affiliate/Fed Gov?  HOST ID CLIENT CODE                     CLIENT NAME         CLIENT AR TPA_y                                Cash
0      Y       7601                           Aetna                NaN                          NaN              Health Care and Social Assistance         NaN                                                NaN                                  NaN   NaN  2017-10-13              NaT          Affiliate      NaN         NaN                             NaN               NaN   NaN                                 NaN
1      Y       1500                      PPC SELECT                NaN                          NaN  Other Services (except Public Administration)         NaN                                                NaN                                  NaN   NaN         NaT              NaT                NaN      NaN         NaN                             NaN               NaN   NaN                                 NaN
2      Y       4270       ATLANTIC GENERAL HOSPITAL              418.0                        418.0              Health Care and Social Assistance    622110.0             General Medical and Surgical Hospitals  Maryland Hospital Association/PRIME   NaN  2006-03-01              NaT          Affiliate      NaN         NaN                             NaN               NaN   NaN                                 NaN
3      Y       1000  SOCIAL SECURITY ADMINISTRATION            60000.0                      70000.0                Federal Government/Associations    923130.0  Administration of Social, Human Resource and I...                                  PPC   EAA  2002-07-01              NaT            Fed Gov   1000.0         SSA  SOCIAL SECURITY ADMINISTRATION  KELLY MENCHINGER   EAA  TPA sends cash on behalf of client
4      Y       3900                   STEPHENS, INC             1000.0                       1000.0                          Finance and Insurance    523110.0          Investment Banking and Securities Dealing                                  PPC   NaN  2002-02-01              NaT          Affiliate      NaN         NaN                             NaN               NaN   NaN                                 NaN

In [12]:
list(Client)

['Active',
 'Client ID',
 'Account Name',
 'Current Eligibles',
 'Eligibles at time of Launch',
 'Industry',
 'NAICS Code',
 'NAICS Description',
 'Broker',
 'TPA_x',
 'Launch Date',
 'Termination Date',
 'Affiliate/Fed Gov?',
 'HOST ID',
 'CLIENT CODE',
 'CLIENT NAME',
 'CLIENT AR',
 'TPA_y',
 'Cash']

In [ ]:
Client_cols = ['Active',
 'Client ID',               
 'Account Name',
'Current Eligibles',
 'Eligibles at time of Launch',
 'Industry',
 'NAICS Code',
 'NAICS Description',
 'Broker',
 'TPA_x',
 'Launch Date',
 'Termination Date',
 'Affiliate/Fed Gov?',
 'Cash']

In [54]:
Client['Active'].value_counts()

Y               334
Terminated      163
Consolidated     10
Split             5
Inactive          2
Name: Active, dtype: int64

In [59]:
Customer.head()

Unique_Customer_ID  Unique_Company_ID Enrollment_Date  Assigned_Spending_Limit  Customer_Tenure  Customer_Salary Prior_Customer_Flag                 Street1 Street2           City State    Zip    Status Term_Date Active  Client ID                    Account Name                         Industry  NAICS Code                                  NAICS Description Broker TPA_x Launch Date Termination Date Affiliate/Fed Gov?                                Cash
0           100001115               1000      02/24/2014                   6880.0            230.0          58229.0        Repeat Buyer          1471 N EAST ST     NaN           YORK    PA  17406  Employed       NaN      Y     1000.0  SOCIAL SECURITY ADMINISTRATION  Federal Government/Associations    923130.0  Administration of Social, Human Resource and I...    PPC   EAA  2002-07-01              NaT            Fed Gov  TPA sends cash on behalf of client
1           100001120               1000      02/24/2014                   6520.0            362.0         109245.0        Repeat Buyer         94 Brentwood Ln     NaN  Valley Stream    NY  11581  Employed       NaN      Y     1000.0  SOCIAL SECURITY ADMINISTRATION  Federal Government/Associations    923130.0  Administration of Social, Human Resource and I...    PPC   EAA  2002-07-01              NaT            Fed Gov  TPA sends cash on behalf of client
2           100001141               1000      02/25/2014                  10290.0            337.0         127226.0        Repeat Buyer  103 KENILWORTH PARK DR  APT 2B         TOWSON    MD  21204  Employed       NaN      Y     1000.0  SOCIAL SECURITY ADMINISTRATION  Federal Government/Associations    923130.0  Administration of Social, Human Resource and I...    PPC   EAA  2002-07-01              NaT            Fed Gov  TPA sends cash on behalf of client
3           100001158               1000      02/24/2014                   5190.0            419.0          49375.0        Repeat Buyer       1036 Braddish Ave     NaN      Baltimore    MD  21216  Employed       NaN      Y     1000.0  SOCIAL SECURITY ADMINISTRATION  Federal Government/Associations    923130.0  Administration of Social, Human Resource and I...    PPC   EAA  2002-07-01              NaT            Fed Gov  TPA sends cash on behalf of client
4           100001169               1000      02/24/2014                   7500.0            448.0          69460.0        Repeat Buyer       3915 W ROGERS AVE     NaN      BALTIMORE    MD  21215  Employed       NaN      Y     1000.0  SOCIAL SECURITY ADMINISTRATION  Federal Government/Associations    923130.0  Administration of Social, Human Resource and I...    PPC   EAA  2002-07-01              NaT            Fed Gov  TPA sends cash on behalf of client

In [ ]:
Customer = Customer.merge(Client[Client_cols],how='left',left_on='Unique_Company_ID',right_on='Client ID')

In [ ]:
Perf = pd.read_csv('./data/Performance_Data_Request_20191204.csv')

In [64]:
list(Perf)

['Unique_Order_ID',
 'Unique_Customer_ID',
 'Order_Amount',
 'Product_Markup',
 'Payments_Due',
 'Current_Balance',
 'Date_account_went_delinquent',
 'Default_Status',
 'Delinquency_Bucket',
 'Losses',
 'Auto_Pay_Enrollment',
 'Order_Closed_Flag',
 'Type_of_Backup_Payment',
 'Spending_Limit_at_time_of_Order',
 'Tenure_at_time_of_Order',
 'Salary_at_time_of_Order',
 'Street1_x',
 'Street2_x',
 'City_x',
 'State_x',
 'Zip_x',
 'items_ordered',
 'Year_and_Month',
 'EMPSTATUS',
 'Order_Date',
 'Year',
 'Unique_Company_ID',
 'Enrollment_Date',
 'Assigned_Spending_Limit',
 'Customer_Tenure',
 'Customer_Salary',
 'Prior_Customer_Flag',
 'Street1_y',
 'Street2_y',
 'City_y',
 'State_y',
 'Zip_y',
 'Status',
 'Term_Date',
 'Active',
 'Client ID',
 'Account Name',
 'Industry',
 'NAICS Code',
 'NAICS Description',
 'Broker',
 'TPA_x',
 'Launch Date',
 'Termination Date',
 'Affiliate/Fed Gov?',
 'Cash']

In [9]:
Perf.shape

(38105255, 25)

In [ ]:
Perf = Perf.merge(Customer, how='left',on='Unique_Customer_ID')

In [14]:
Perf['Year_and_Month'] = pd.to_datetime(Perf['Year_and_Month'].astype(str), format = '%Y%m')
Perf['YQ'] = pd.PeriodIndex(Perf['Year_and_Month'], freq='Q')

In [10]:
Perf.head()

Unique_Order_ID  Unique_Customer_ID Order_Amount Product_Markup Payments_Due  Current_Balance Date_account_went_delinquent Default_Status Delinquency_Bucket  Losses Auto_Pay_Enrollment Order_Closed_Flag Type_of_Backup_Payment Spending_Limit_at_time_of_Order Tenure_at_time_of_Order Salary_at_time_of_Order        Street1_x Street2_x      City_x State_x    Zip_x                                      items_ordered Year_and_Month EMPSTATUS  Order_Date  Unique_Company_ID Enrollment_Date  Assigned_Spending_Limit  Customer_Tenure  Customer_Salary Prior_Customer_Flag        Street1_y Street2_y      City_y State_y  Zip_y    Status Term_Date Active  Client ID                                       Account Name                         Industry  NAICS Code NAICS Description Broker TPA_x Launch Date Termination Date Affiliate/Fed Gov? Cash      YQ
0        10000091           100486182      1072.88              .        40.11           907.86                            .        Current            000-000     0.0                  PA                 N                    ACH                            96.6                     327                  800.29  929 IMPERIAL CT       NaN  HALETHORPE      MD  21227.0  DeWalt 12in 15-Amp Double-Bevel Compound Miter...     2014-04-01  Employed  03/15/2014             2049.0      02/25/2014                   9660.0            327.0          80029.0        Repeat Buyer  929 IMPERIAL CT       NaN  HALETHORPE      MD  21227  Employed       NaN      Y     2049.0  FEDERAL GOVERNMENT/POSTAL WORKERS/NIH/DEPT OF ...  Federal Government/Associations         NaN               NaN    NaN   NaN  2002-07-01              NaT            Fed Gov  NaN  2014Q2
1        10000091           100486182      1072.88              .        40.11           817.86                            .        Current            000-000     0.0                  PA                 N                    ACH                            96.6                     327                  800.29  929 IMPERIAL CT       NaN  HALETHORPE      MD  21227.0  DeWalt 12in 15-Amp Double-Bevel Compound Miter...     2014-05-01  Employed  03/15/2014             2049.0      02/25/2014                   9660.0            327.0          80029.0        Repeat Buyer  929 IMPERIAL CT       NaN  HALETHORPE      MD  21227  Employed       NaN      Y     2049.0  FEDERAL GOVERNMENT/POSTAL WORKERS/NIH/DEPT OF ...  Federal Government/Associations         NaN               NaN    NaN   NaN  2002-07-01              NaT            Fed Gov  NaN  2014Q2
2        10000091           100486182      1072.88              .        40.11           727.86                            .        Current            000-000     0.0                  PA                 N                    ACH                            96.6                     327                  800.29  929 IMPERIAL CT       NaN  HALETHORPE      MD  21227.0  DeWalt 12in 15-Amp Double-Bevel Compound Miter...     2014-06-01  Employed  03/15/2014             2049.0      02/25/2014                   9660.0            327.0          80029.0        Repeat Buyer  929 IMPERIAL CT       NaN  HALETHORPE      MD  21227  Employed       NaN      Y     2049.0  FEDERAL GOVERNMENT/POSTAL WORKERS/NIH/DEPT OF ...  Federal Government/Associations         NaN               NaN    NaN   NaN  2002-07-01              NaT            Fed Gov  NaN  2014Q2
3        10000091           100486182      1072.88              .        40.11           637.86                            .        Current            000-000     0.0                  PA                 N                    ACH                            96.6                     327                  800.29  929 IMPERIAL CT       NaN  HALETHORPE      MD  21227.0  DeWalt 12in 15-Amp Double-Bevel Compound Miter...     2014-07-01  Employed  03/15/2014             2049.0      02/25/2014                   9660.0            327.0          80029.0        Repeat Buyer  929 IMPERIAL CT       NaN  HALETHORPE      MD  2122

### FPD Analysis

In [48]:
def FPD(df,ID,balance_ind,period=1):
    df_sub = df.groupby(ID).head(period+1)
    df_sub['diff'] = df_sub[balance_ind].diff(-1*period)
    final = pd.DataFrame(df_sub.values[::period+1],index = df_sub.index[::period+1])
    final.columns = list(df_sub)
    return final



def check_FDP(df,FPD_df,balance_ind,file_name):
    df_1 = df.loc[df.groupby('Unique_Order_ID')['Year_and_Month'].idxmin()]
    df_sub = df_1.merge(FPD_df[['Unique_Order_ID','diff']],how = 'left', on= 'Unique_Order_ID')
    df_sub['FPD_flag'] = df_sub['diff'].apply(lambda x: 1 if x == 0 else 0)
    df_sub['FPD_Loss'] = df_sub['FPD_flag']*df_sub[balance_ind]
    df_sub['Year_and_Month'] = df_sub['Year_and_Month'].apply(lambda x: pd.to_datetime(str(x),format = '%Y%m'))
    df_sub.groupby('Year_and_Month').agg({'Unique_Order_ID':'count','FPD_flag':'sum',balance_ind:'sum','FPD_Loss':'sum'}).to_csv('./data/{}.csv'.format(file_name))

    return df_sub.groupby('Year_and_Month').agg({'Unique_Order_ID':'count','FPD_flag':'sum',balance_ind:'sum','FPD_Loss':'sum'}).reset_index()

In [50]:
FPD2 = FPD(Perf,'Unique_Order_ID','Current_Balance',2 )
DQ151_FPD2 = check_FDP(Perf[Perf['Delinquency_Bucket']=='151+'],FPD2,'Current_Balance','DQ151_FPD2')
DQ151_FPD2

Year_and_Month  Unique_Order_ID  FPD_flag  Current_Balance   FPD_Loss
0      2012-06-01                3         0          2330.50       0.00
1      2012-07-01               14         0         14078.85       0.00
2      2012-08-01               99         2        117518.64    1763.58
3      2012-09-01              195        20        250116.27   39387.82
4      2012-10-01              277        23        308757.91   32279.52
5      2012-11-01              384        26        426702.43   36546.52
6      2012-12-01              506        30        492725.00   40381.52
7      2013-01-01              683        43        647852.15   59893.12
8      2013-02-01              757        36        665811.24   43236.52
9      2013-03-01              937        44        804384.29   48146.01
10     2013-04-01              987        47        817048.19   51616.38
11     2013-05-01              979        40        773054.18   45611.50
12     2013-06-01             1119        46        827352.49   48607.81
13     2013-07-01             1833       111       1444218.22  120952.90
14     2013-08-01             1883        80       1344531.96   72941.22
15     2013-09-01             1872        71       1225053.57   64736.23
16     2013-10-01             2201        73       1430272.46   74790.67
17     2013-11-01             2191        67       1384627.80   63672.03
18     2013-12-01             2568       135       1369733.12   92969.58
19     2014-01-01             2692        91       1517573.71   73897.96
20     2014-02-01             1724        64        928634.62   48608.47
21     2014-03-01             2176        89       1194458.73   70158.90
22     2014-04-01             2017        90       1108802.69   84274.64
23     2014-05-01             1705        77        909278.32   59993.57
24     2014-06-01             1609        82        897773.83   65447.52
25     2014-07-01             2152       110       1397826.93   88967.03
26     2014-08-01             2501        96       1628542.32   80262.20
27     2014-09-01             2359        72       1447032.68   66768.41
28     2014-10-01             2423        75       1392908.01   59079.08
29     2014-11-01             2330        88       1330066.45   80195.86
30     2014-12-01             3035       112       1661857.33   98187.21
31     2015-01-01             2822       127       1479772.41  109643.71
32     2015-02-01             2501       102       1270698.34   98679.45
33     2015-03-01             2768       113       1491022.29  110042.35
34     2015-04-01             2392        87       1205158.54   97760.76
35     2015-05-01             2232        84       1220029.88   61587.58
36     2015-06-01             2369       110       1504585.21   96685.67
37     2015-07-01             2766       173       1841103.07  170511.39
38     2015-08-01             2960       113       1864655.46  112578.38
39     2015-09-01             3037        86       1844481.60   80614.95
40     2015-10-01             2846        92       1682240.01   72018.96
41     2015-11-01             3289       113       1802198.25  108765.03
42     2015-12-01             3845       112       1987596.89   92230.91
43     2016-01-01             4047       134       2123583.43  123708.33
44     2016-02-01             3580       123       1777830.55   93778.74
45     2016-03-01             3879       108       2002288.41   94198.26
46     2016-04-01             3655        77       1765698.50   61331.94
47     2016-05-01             3321        63       1660100.28   37126.91
48     2016-06-01             3152        81       1746192.68   63279.37
49     2016-07-01             3668       139       2131754.03  115829.40
50     2016-08-01             4256       107       2264931.25   92928.13
51     2016-09-01             4306       112       2100040.57   85117.70
52     2016-10-01             4574       105       2238153.41   94590.70
53     2016-11-01             5280       108       2580987.80

In [49]:
CO_FPD2 = check_FDP(Perf[Perf['Default_Status']=='Chargeoff'],FPD2,'Losses','CO_FPD2')
CO_FPD2

Year_and_Month  Unique_Order_ID  FPD_flag      Losses   FPD_Loss
0      2012-06-01                1         0      970.06       0.00
1      2012-07-01               20         3    25681.11    3651.20
2      2012-08-01               25         4    27486.75    4790.32
3      2012-09-01              132         7   138019.87    9115.84
4      2012-10-01              148        11   170685.53    8226.12
5      2012-11-01               69         3    86988.76    4275.82
6      2012-12-01              202        12   235741.70   21530.16
7      2013-01-01               68         4    72514.83    7133.75
8      2013-02-01               45         8    58550.44   14952.72
9      2013-03-01              430        15   405798.85   20335.24
10     2013-04-01             1105        86  1062676.20  118213.69
11     2013-05-01              883        39   778367.64   56201.73
12     2013-06-01              739        38   587021.69   41898.89
13     2013-07-01              748        56   650543.97   77493.44
14     2013-08-01             1249        70  1016323.94   91678.98
15     2013-09-01             1184        64   945028.77   59080.85
16     2013-10-01             2305       105  1758702.40  102579.59
17     2013-11-01             1953        86  1288438.75   85890.22
18     2013-12-01             1318        27   924049.56   26604.81
19     2014-01-01             2327       106  1463982.24  101946.59
20     2014-02-01             2690        80  1551256.00   71186.87
21     2014-03-01             1097        63   640249.10   47116.16
22     2014-04-01             2023        99  1113631.47   79623.40
23     2014-05-01             2435        87  1482195.99   93610.99
24     2014-06-01             1583        64   914040.00   67587.04
25     2014-07-01             1614        77   991094.80   62546.64
26     2014-08-01             1724        69  1111419.06   60740.86
27     2014-09-01             2073        77  1294410.44   65381.74
28     2014-10-01             2785       105  1667787.35   89204.70
29     2014-11-01             2841        85  1701550.90   73618.37
30     2014-12-01             1752        57  1008815.05   42730.59
31     2015-01-01             2621       111  1509195.72   96814.97
32     2015-02-01             2316       125  1311404.87  122080.70
33     2015-03-01             2342        82  1229308.80   88111.61
34     2015-04-01             2279       120  1221184.71  104158.57
35     2015-05-01             2479       102  1341745.32  111886.71
36     2015-06-01             2614       130  1453975.92  114687.43
37     2015-07-01             1742        83  1062487.01   65086.83
38     2015-08-01             2454       175  1462460.68  149422.95
39     2015-09-01             2368       111  1416969.17  111155.78
40     2015-10-01             3183       105  1852340.06   89307.07
41     2015-11-01             2559        97  1514460.84   86004.70
42     2015-12-01             1911        86  1106766.86   80944.30
43     2016-01-01             2452       112  1359596.40   84894.62
44     2016-02-01             2139        91  1206035.92   85359.10
45     2016-03-01             2770       113  1511262.69   99595.69
46     2016-04-01             3122       117  1683036.48   97483.90
47     2016-05-01             3808        97  1884281.98   83684.22
48     2016-06-01             5413       127  2775596.71   89394.06
49     2016-07-01             3480       118  1811466.95   85916.22
50     2016-08-01             1443        43   753925.40   28295.98
51     2016-09-01             2509        95  1353161.94   80145.50
52     2016-10-01             3709       181  2135365.22  158527.50
53     2016-11-01             3987       161  2023782.36  126209.70
54     2016-12-01             3647        86  1758902.95   65841.59
55     2017-01-01             2693        71  1336660.74   51444.91
56     2017-02-01             5911       170  2777364.32  127747.49
57     2017-03-01             5478       153  2497101.54  1

In [5]:
top2 = Perf.groupby('Unique_Order_ID').head(2)

In [6]:
top2['diff'] = top2['Current_Balance'].diff(-1)

In [7]:
final_df = pd.DataFrame(top2.values[::2],index=top2.index[::2])
final_df.columns = list(top2)

In [33]:
final_df.head()

Unique_Order_ID Unique_Customer_ID Order_Amount Product_Markup Payments_Due Current_Balance Date_account_went_delinquent Default_Status Delinquency_Bucket Losses Auto_Pay_Enrollment Order_Closed_Flag Type_of_Backup_Payment Spending_Limit_at_time_of_Order Tenure_at_time_of_Order Salary_at_time_of_Order            Street1 Street2           City State    Zip                                      Items_Ordered Year_and_month     diff
0         11478280        1.00001e+08       691.12          359.9        26.58          685.72                   06/30/2015        Current            000-000      0                  PD                 N                    ACH                            6880                     230                   58229     1471 N EAST ST     NaN           YORK    PA  17406  Movado Men's Bold Watch With Tr90 Composite Ma...         201501        0
11  SSAZIMM1436202        1.00001e+08       360.53            NaN        13.86          333.36                          NaN        Current            000-000      0                  PD                 N                    ACH                            6880                     230                   58229  1634 Shadyside Rd     NaN      Baltimore    MD  21218  Crescendo Fitness Magnetic Resistance Exercise...         201312        0
15        10425611        1.00001e+08      2821.78            NaN       108.53         2821.78                          NaN        Current            000-000      0                  PD                 N                    ACH                            6520                     362                  109245      7608 270TH ST     NaN  NEW HYDE PARK    NY  11040  Char-Broil 2-Burner Gas Grill with Side Burner...         201405   108.53
27        10871644        1.00001e+08       4721.7            NaN        181.6          4441.6                          NaN        Current            000-000      0                  PD                 N                    ACH                            6520                     362                  109245       1401 Kew Ave     NaN        Hewlett    NY  11557  Delamore 3/8 CT TW White Diamond Stud Earrings...         201409   728.48
39        10995108        1.00001e+08       806.57            NaN        89.55         2199.72                          NaN        Current            000-000      0                  PD                 N                    ACH                            6520                     362                  109245       1401 Kew Ave     NaN        Hewlett    NY  11557  KitchenAid KFC3511CU Contour Silver 3.5 Cup Fo...         201410  1505.04

In [70]:
DQ151 = Perf[Perf['Delinquency_Bucket']=='151+']
DQ151 = DQ151.loc[DQ151.groupby('Unique_Order_ID')['Year_and_month'].idxmin()]
DQ151_diff = DQ151.merge(final_df[['Unique_Order_ID','diff']],how='left',on='Unique_Order_ID')
DQ151_diff['FPD_flag'] = DQ151_diff['diff'].apply(lambda x: 1 if x == 0 else 0)
DQ151_diff['FPD_Loss'] = DQ151_diff['FPD_flag']*DQ151_diff['Current_Balance']
DQ151_diff['Year_and_month'] = DQ151_diff['Year_and_month'].apply(lambda x: pd.to_datetime(str(int(x)),format = '%Y%m'))
DQ151_diff.groupby('Year_and_month').agg({'Unique_Order_ID':'count','FPD_flag':'sum','Current_Balance':'sum','FPD_Loss':'sum'})

Unique_Order_ID  FPD_flag  Current_Balance   FPD_Loss
Year_and_month                                                       
2012-06-01                    3         1          2330.50    1197.50
2012-07-01                   14         2         14078.85     731.66
2012-08-01                   99        11        117518.64   16537.09
2012-09-01                  195        29        250116.27   44563.09
2012-10-01                  277        44        308757.91   57396.70
2012-11-01                  384        59        426702.43   83897.78
2012-12-01                  506        83        492725.00   89699.05
2013-01-01                  683        91        647852.15  117923.74
2013-02-01                  757       106        665811.24  110103.95
2013-03-01                  937       135        804384.29  126781.99
2013-04-01                  987       128        817048.19  128373.84
2013-05-01                  979       122        773054.18  125954.79
2013-06-01                 1119       141        827352.49  130901.80
2013-07-01                 1833       285       1444218.22  293906.69
2013-08-01                 1883       214       1344531.96  200034.37
2013-09-01                 1872       214       1225053.57  156311.82
2013-10-01                 2201       216       1430272.46  165728.91
2013-11-01                 2191       210       1384627.80  159268.67
2013-12-01                 2568       356       1369733.12  196106.90
2014-01-01                 2692       256       1517573.71  164988.46
2014-02-01                 1724       202        928634.62  147370.54
2014-03-01                 2176       278       1194458.73  211544.51
2014-04-01                 2017       207       1108802.69  165770.81
2014-05-01                 1705       202        909278.32  133281.90
2014-06-01                 1609       176        897773.83  113039.56
2014-07-01                 2152       299       1397826.93  211059.68
2014-08-01                 2501       285       1628542.32  230253.38
2014-09-01                 2359       232       1447032.68  159081.72
2014-10-01                 2423       233       1392908.01  167683.28
2014-11-01                 2330       208       1330066.45  145825.43
2014-12-01                 3035       314       1661857.33  213915.14
2015-01-01                 2822       269       1479772.41  195533.76
2015-02-01                 2501       241       1270698.34  163465.13
2015-03-01                 2768       273       1491022.29  202896.61
2015-04-01                 2392       264       1205158.54  193104.27
2015-05-01                 2232       258       1220029.88  179169.57
2015-06-01                 2369       313       1504585.21  239014.17
2015-07-01                 2766       348       1841103.07  314662.22
2015-08-01                 2960       311       1864655.46  242886.25
2015-09-01                 3037       277       1844481.60  221126.04
2015-10-01                 2846       245       1682240.01  177010.74
2015-11-01                 3289       275       1802198.25  179529.67
2015-12-01                 3845       305       1987596.89  210756.29
2016-01-01                 4047       370       2123583.43  266284.73
2016-02-01                 3580       319       1777830.55  234002.96
2016-03-01                 3879       367       2002288.41  273613.15
2016-04-01                 3655       307       1765698.50  210008.55
2016-05-01                 3321       283       1660100.28  183793.77
2016-06-01                 3152       226       1746192.68  137767.71
2016-07-01                 3668       277       2131754.03  221734.94
2016-08-01                 4256       263       2264931.25  192529.53
2016-09-01                 4306       288       2100040.57  185814.50
2016-10-01                 4574       290       2238153.41  195978.48
2016-11-01                 5278       355       2580222.89  256037.76
2016-12-01                 4853       405       2239495.52  255835.34
2017-01-01                

In [72]:
DQ151_diff.groupby('Year_and_month').agg({'Unique_Order_ID':'count','FPD_flag':'sum','Current_Balance':'sum','FPD_Loss':'sum'}).reset_index().to_csv('./data/FDP_DQ151.csv',index = False)

In [34]:
DQ151_diff.shape

(1547690, 26)

In [37]:
DQ151_diff.Unique_Order_ID.nunique()

365503

In [ ]:
df.loc[df.groupby('a')['b'].idxmax()]

(291765, 23)

In [75]:
CO = Perf[Perf['Default_Status']=='Chargeoff']
CO = CO.loc[CO.groupby('Unique_Order_ID')['Year_and_month'].idxmin()]
CO_diff = CO.merge(final_df[['Unique_Order_ID','diff']],how='left',on='Unique_Order_ID')
CO_diff['FPD_flag'] = CO_diff['diff'].apply(lambda x: 1 if x == 0 else 0)
CO_diff['FPD_Loss'] = CO_diff['FPD_flag']*CO_diff['Losses']
CO_diff['Year_and_month'] = CO_diff['Year_and_month'].apply(lambda x: pd.to_datetime(str(int(x)),format = '%Y%m'))
CO_diff.groupby('Year_and_month').agg({'Unique_Order_ID':'count','FPD_flag':'sum','Losses':'sum','FPD_Loss':'sum'})

Unique_Order_ID  FPD_flag      Losses   FPD_Loss
Year_and_month                                                  
2012-06-01                    1         1      970.06     970.06
2012-07-01                   20         6    25681.11    4972.10
2012-08-01                   25         8    27486.75    6336.40
2012-09-01                  132        28   138019.87   30443.74
2012-10-01                  148        32   170685.53   38285.36
2012-11-01                   69        15    86988.76   16649.47
2012-12-01                  202        38   235741.70   53667.79
2013-01-01                   68        10    72514.83   13388.76
2013-02-01                   45        11    58550.44   16378.41
2013-03-01                  430        64   405798.85   73143.93
2013-04-01                 1105       185  1062676.20  222131.26
2013-05-01                  883       120   778367.64  126624.07
2013-06-01                  739        93   587021.69   88007.68
2013-07-01                  748       117   650543.97  129819.31
2013-08-01                 1249       181  1016323.94  207717.27
2013-09-01                 1184       178   945028.77  181766.99
2013-10-01                 2305       292  1758702.40  271949.23
2013-11-01                 1953       196  1288438.75  155118.06
2013-12-01                 1318       132   924049.56  114507.62
2014-01-01                 2327       280  1463982.24  205293.62
2014-02-01                 2690       242  1551256.00  180551.44
2014-03-01                 1097       160   640249.10  104040.43
2014-04-01                 2023       247  1113631.47  171669.59
2014-05-01                 2435       258  1482195.99  236011.53
2014-06-01                 1583       189   914040.00  144406.05
2014-07-01                 1614       193   991094.80  148323.04
2014-08-01                 1724       201  1111419.06  152226.02
2014-09-01                 2073       265  1294410.44  198714.30
2014-10-01                 2785       293  1667787.35  212980.05
2014-11-01                 2841       268  1701550.90  200848.69
2014-12-01                 1752       178  1008815.05  126957.75
2015-01-01                 2621       274  1509195.72  193575.93
2015-02-01                 2316       249  1311404.87  211186.82
2015-03-01                 2342       208  1229308.80  127932.36
2015-04-01                 2279       228  1221184.71  168620.88
2015-05-01                 2479       274  1341745.32  201292.58
2015-06-01                 2614       322  1453975.92  238116.37
2015-07-01                 1742       228  1062487.01  174395.17
2015-08-01                 2454       347  1462460.68  269045.93
2015-09-01                 2368       248  1416969.17  206139.83
2015-10-01                 3183       317  1852340.06  239527.06
2015-11-01                 2559       234  1514460.84  191247.08
2015-12-01                 1911       194  1106766.86  135356.20
2016-01-01                 2452       286  1359596.40  193327.61
2016-02-01                 2139       228  1206035.92  181088.07
2016-03-01                 2770       305  1511262.69  216042.04
2016-04-01                 3122       313  1683036.48  233887.87
2016-05-01                 3808       327  1884281.98  232140.69
2016-06-01                 5413       470  2775596.71  299716.26
2016-07-01                 3480       291  1811466.95  174760.43
2016-08-01                 1443       142   753925.40  111268.36
2016-09-01                 2509       207  1353161.94  149773.97
2016-10-01                 3709       396  2135365.22  320995.06
2016-11-01                 3987       334  2023782.36  228247.15
2016-12-01                 3647       286  1758902.95  182191.16
2017-01-01                 2693       227  1336660.74  163786.35
2017-02-01                 5911       489  2777364.32  357856.79
2017-03-01                 5477       410  2497587.92  270058.10
2017-04-01                 2604       232  1168893.97  135515.46
2017-05-01                 1998       141   920113.

In [38]:
CO.shape

(351166, 23)

In [39]:
CO.Unique_Order_ID.nunique()

291765

In [74]:
CO_diff.head()

Unique_Order_ID  Unique_Customer_ID  Order_Amount  Product_Markup  Payments_Due  Current_Balance Date_account_went_delinquent Default_Status Delinquency_Bucket   Losses Auto_Pay_Enrollment Order_Closed_Flag Type_of_Backup_Payment  Spending_Limit_at_time_of_Order  Tenure_at_time_of_Order  Salary_at_time_of_Order             Street1 Street2         City State      Zip                                      Items_Ordered Year_and_month     diff  FPD_flag  FPD_Loss
0        10211496         300128027.0        847.42             NaN         35.31              0.0                   08/31/2014      Chargeoff            000-000   734.48                  PD                 Y                    ACH                           2425.0                     89.0                  21902.4  1044 E HARMONY AVE     NaN         MESA    AZ  85204.0  SquareTrade 2-Year MP3 Warranty; Kenwood eXcel...     2015-01-01     6.73         0       0.0
1        10212837         300128221.0        724.14             NaN         30.17              0.0                   09/30/2014      Chargeoff            000-000   663.74                  PA                 Y                    ACH                           6120.0                    193.0                  68320.2     8421 FOWLER AVE     NaN    PENSACOLA    FL  32534.0  SquareTrade 2-Year iPad Tablet Warranty Plus A...     2015-03-01 -1172.76         0       0.0
2        10213575         300128208.0        785.80             NaN         15.11              0.0                   02/28/2015      Chargeoff            000-000   241.76                  PD                 Y                    ACH                           2260.0                    116.0                  29473.6     2243 HWY 41A  N     NaN  SHELBYVILLE    TN  37160.0  Microsoft Xbox One, Titanfall Game, Wireless C...     2015-07-01   370.56         0       0.0
3        10215298         300128167.0        778.79             NaN         14.98              0.0                   09/30/2014      Chargeoff            000-000   628.64                  PD                 Y                    ACH                            845.0                     82.0                  21528.0   1441 hartford hwy     e16       dothan    AL  36301.0  Norton 360 All-In-One Security Suite; HP 15 15...     2015-05-01  -516.56         0       0.0
4        10217158         300128289.0       1300.05             NaN         25.00              0.0                   07/31/2014      Chargeoff            000-000  1200.00                  PD                 Y                    ACH                           2750.0                     88.0                  25272.0    2109 BISMARCK ST     NaN       VERNON    TX  76384.0  Samsung Galaxy Tab 3 White 10.1in Display 16GB...     2014-11-01   841.44         0       0.0

In [77]:
CO_diff.groupby('Year_and_month').agg({'Unique_Order_ID':'count','FPD_flag':'sum','Losses':'sum','FPD_Loss':'sum'}).reset_index().to_csv('./data/FDP_CO.csv',index = False)

In [20]:
Perf.head()

Unique_Order_ID  Unique_Customer_ID  Order_Amount  Product_Markup  Payments_Due  Current_Balance Date_account_went_delinquent Default_Status Delinquency_Bucket  Losses Auto_Pay_Enrollment Order_Closed_Flag Type_of_Backup_Payment  Spending_Limit_at_time_of_Order  Tenure_at_time_of_Order  Salary_at_time_of_Order         Street1 Street2  City State      Zip                                      Items_Ordered  Year_and_month
0        11478280         100001115.0        691.12           359.9         26.58           685.72                   06/30/2015        Current            000-000     0.0                  PD                 N                    ACH                           6880.0                    230.0                  58229.0  1471 N EAST ST     NaN  YORK    PA  17406.0  Movado Men's Bold Watch With Tr90 Composite Ma...        201501.0
1        11478280         100001115.0        691.12           359.9         26.58           685.72                   06/30/2015        Current            000-000     0.0                  PD                 N                    ACH                           6880.0                    230.0                  58229.0  1471 N EAST ST     NaN  YORK    PA  17406.0  Movado Men's Bold Watch With Tr90 Composite Ma...        201502.0
2        11478280         100001115.0        691.12           359.9         26.58           685.72                   06/30/2015        Current            000-000     0.0                  PD                 N                    ACH                           6880.0                    230.0                  58229.0  1471 N EAST ST     NaN  YORK    PA  17406.0  Movado Men's Bold Watch With Tr90 Composite Ma...        201503.0
3        11478280         100001115.0        691.12           359.9         26.58           685.72                   06/30/2015        001-030            001-030     0.0                  PD                 N                    ACH                           6880.0                    230.0                  58229.0  1471 N EAST ST     NaN  YORK    PA  17406.0  Movado Men's Bold Watch With Tr90 Composite Ma...        201504.0
4        11478280         100001115.0        691.12           359.9         26.58           658.72                   06/30/2015        001-030            001-030     0.0                  PD                 N                    ACH                           6880.0                    230.0                  58229.0  1471 N EAST ST     NaN  YORK    PA  17406.0  Movado Men's Bold Watch With Tr90 Composite Ma...        201505.0

In [21]:
Perf[Perf['Order_Closed_Flag']=='Y'].groupby('Default_Status').size()

Default_Status
001-030           102
031-060            34
061-090            12
091-120            12
121-150             7
151+               21
Bankruptcy      16880
Chargeoff      291607
Current       2203621
Fraud           11006
dtype: int64

In [22]:
Perf[Perf['Order_Closed_Flag']=='N'].groupby('Default_Status').size()

Default_Status
001-030        2949700
031-060         816738
061-090         583076
091-120         481314
121-150         425623
151+           1435981
Bankruptcy      189727
Chargeoff        59559
Current       28488323
Fraud           146522
dtype: int64

In [24]:
# Perf[Perf['Order_Closed_Flag']=='N'].groupby(['Year_and_month','Default_Status']).size()

In [25]:
Perf.Order_Closed_Flag.value_counts()

N    35576563
Y     2523302
Name: Order_Closed_Flag, dtype: int64

In [27]:
Perf.groupby('Order_Closed_Flag').agg({'Unique_Order_ID':'nunique'})

Unique_Order_ID
Order_Closed_Flag                 
N                          3125150
Y                          2522465

In [28]:
Perf[Perf['Order_Closed_Flag']=='Y']['Current_Balance'].value_counts()

0.0    2523302
Name: Current_Balance, dtype: int64

In [29]:
Perf[Perf['Current_Balance']==0]['Unique_Order_ID'].nunique()

2522465

In [30]:
Perf[Perf['Current_Balance']==0].shape

(2523673, 23)

In [47]:
final_df.Unique_Order_ID.nunique() == final_df.shape[0]

True

In [48]:
FPD_Order_IDs = final_df.Unique_Order_ID.tolist()

In [50]:
FPD_Closed = Perf[(Perf['Unique_Order_ID'].isin(FPD_Order_IDs)) & (Perf['Order_Closed_Flag']=='Y')]

In [51]:
FPD_Closed.shape[0]

2486632

In [52]:
FPD_Closed.Unique_Order_ID.nunique() == FPD_Closed.shape[0]

False

In [53]:
FPD_Closed.Unique_Order_ID.nunique()

2485795

In [54]:
FPD_Closed.loc[FPD_Closed.groupby('Unique_Order_ID')['Year_and_month'].idxmax()].shape

(2485795, 23)

In [58]:
FPD_Closed = FPD_Closed.loc[FPD_Closed.groupby('Unique_Order_ID')['Year_and_month'].idxmax()]

In [61]:
FPD_Closed['Default_Status'].value_counts()

Current       2166378
Chargeoff      291536
Bankruptcy      16856
Fraud           10838
001-030           101
031-060            34
151+               21
091-120            12
061-090            12
121-150             7
Name: Default_Status, dtype: int64

In [64]:
FPD_Closed[FPD_Closed['Default_Status'].isin(['Chargeoff','Current'])].groupby('Year_and_month')['Default_Status'].value_counts()#.agg({'Unique_Order_ID':'count','Default_Status':'value_counts'})

Year_and_month  Default_Status
201202.0        Current               3
201203.0        Current               9
201204.0        Current              12
201205.0        Current              28
201206.0        Current              45
                Chargeoff             1
201207.0        Current              78
                Chargeoff            20
201208.0        Current             166
                Chargeoff            25
201209.0        Current             229
                Chargeoff           132
201210.0        Current             407
                Chargeoff           148
201211.0        Current             614
                Chargeoff            69
201212.0        Current            1176
                Chargeoff           202
201301.0        Current            4875
                Chargeoff            68
201302.0        Current            6715
                Chargeoff            45
201303.0        Current            8443
                Chargeoff           430
201304.0 

In [69]:
FPD_Closed[FPD_Closed['Default_Status'].isin(['Chargeoff','Current'])].pivot_table(values = 'Unique_Order_ID',index = 'Year_and_month',columns = 'Default_Status',aggfunc='count',margins=True).reset_index().rename_axis(None, axis=1).to_csv('./data/FPD_Perf.csv',index = False)

### 12.3
### Roll Rate Analysis

In [13]:
Perf['Year'] = Perf['Year_and_Month'].apply(lambda x: str(x)[:4])

In [7]:
# Perf.groupby('Year').agg({'Unique_Order_ID':'nunique'}).reset_index()

Year  Unique_Order_ID
0  2012           181713
1  2013           406501
2  2014           525692
3  2015           665404
4  2016           853597
5  2017          1016059
6  2018          1252077
7  2019          1170246

In [14]:
Perf.groupby('Year').agg({'Unique_Order_ID':'nunique'}).reset_index()

Year  Unique_Order_ID
0  2012           181713
1  2013           406501
2  2014           525691
3  2015           665401
4  2016           853626
5  2017          1016191
6  2018          1252249
7  2019          1170415

In [15]:
# RR = Perf[(Perf['Year'].isin(['2017','2018','2019']))|(Perf['Year_and_Month']==201612)]

In [10]:
RR = Perf[Perf['Year_and_Month']>'2016-12-01T00:00:00.000000000']

In [6]:
# # RR = Perf[Perf['Year'].isin(['2017','2018','2019'])]
# RR['Year_and_month'] = RR['Year_and_month'].apply(lambda x: pd.to_datetime(str(int(x)),format = '%Y%m'))
# RR.groupby('Year_and_month').agg({'Delinquency_Bucket':'count'}).reset_index()
# # Perf.groupby('Year_and_month').agg('Unique_Order_ID':'count')

In [13]:
# get the list of year_and_month, 2016-12 to 2019-10
ym = list(RR['Year_and_Month'].unique())
# list of group combo
roll_group = ['000-000 to 001-030','001-030 to 031-060','031-060 to 061-090','061-090 to 091-120','091-120 to 121-150','121-150 to 151+']

### Use `Delinquency_Bucket` as the DQ indicator

In [15]:
def rr(df, year_month_1,year_month_2):
#     print("{} to {}".format(year_month_1,year_month_2))
    return df[df['Year_and_Month']==year_month_1].merge(df[df['Year_and_Month']==year_month_2],how = 'left', on = 'Unique_Order_ID')

### Roll Rate Matrix - 1 month, 3 month, ...

#### Unit Level

In [41]:
def rr_matrix(df,ym,period):
    l = []
    for i in range(len(ym)):
        if i + period > len(ym)-1:
            break
        else:
            dfs = rr(df,ym[i],ym[i+period])
            dfss = dfs.pivot_table(values = 'Unique_Order_ID',index = 'Delinquency_Bucket_y',columns = 'Delinquency_Bucket_x',aggfunc='count').rename_axis(None, axis=1)
            l.append(dfss)
    return l

In [29]:
matrix_1m = rr_matrix(RR,ym,1)

In [ ]:
# sum([matrix_1m[i] for i in range(24,30)])/6

In [42]:
matrix_3m = rr_matrix(RR,ym,3)

In [44]:
len(matrix_3m)

31

In [54]:
sum([matrix_3m[i] for i in range(24,30)])/6

000-000       001-030      031-060      061-090      091-120      121-150          151+
Delinquency_Bucket_y                                                                                               
000-000               417834.000000  26266.000000  1321.166667   892.666667   644.833333   712.166667   6577.000000
001-030                28726.000000  13449.833333  1042.166667   191.666667    47.333333     7.500000           NaN
031-060                11306.833333   3155.333333  1320.500000   320.166667    88.333333    19.333333      4.833333
061-090                 8346.333333   2514.166667   985.500000   562.833333   139.000000    33.666667     20.166667
091-120                  580.500000   8509.500000  1180.500000   567.000000   293.500000    67.000000     33.833333
121-150                   18.166667    595.333333  8128.666667   832.500000   346.166667   194.166667     69.833333
151+                       5.833333     10.166667   500.333333  8310.333333  8718.166667  8380.666667  14491.833333

#### $ Level

In [11]:
def rr_matrix_bal(df, ym,period):
    l = []
    for i in range(len(ym)):
        if i + period > len(ym)-1:
            break
        else:
            dfs = rr(df,ym[i],ym[i+period])
            dfss = dfs.pivot_table(values = 'Current_Balance_x',index = 'Delinquency_Bucket_y',columns = 'Delinquency_Bucket_x',aggfunc='sum').rename_axis(None, axis=1)
            l.append(dfss)
    
    return l

In [14]:
matrix_1m_bal = rr_matrix_bal(RR,ym,1)

In [21]:
sum([matrix_1m_bal[i] for i in range(6)])/6

000-000       001-030       031-060       061-090       091-120       121-150          151+
Delinquency_Bucket_y                                                                                                  
000-000               1.838328e+08  6.608870e+06  2.033207e+05  6.431713e+04  4.615153e+04  7.881358e+04  1.692778e+06
001-030               1.197147e+07  1.008772e+07  4.637027e+05  3.592429e+04  8.533142e+03  1.566825e+03           NaN
031-060               1.978351e+05  4.020730e+06  1.534830e+06  1.718615e+05  1.121220e+04  3.545280e+03           NaN
061-090               1.044018e+04  6.741361e+04  3.202978e+06  7.258053e+05  8.114971e+04  9.474682e+03           NaN
091-120               2.678787e+03  2.426518e+03  6.979510e+04  2.748737e+06  3.725453e+05  4.467388e+04  5.770258e+03
121-150               9.801017e+02           NaN  1.754303e+03  5.244613e+04  2.429713e+06  2.472656e+05  3.523623e+04
151+                  8.923617e+02           NaN           NaN  1.649922e+03  5.956865e+04  2.221859e+06  7.304536e+06

In [16]:
matrix_3m_bal = rr_matrix_bal(RR,ym,3)

In [22]:
sum([matrix_3m_bal[i] for i in range(24,30)])/6

000-000       001-030       031-060       061-090       091-120       121-150          151+
Delinquency_Bucket_y                                                                                                  
000-000               1.980084e+08  1.154595e+07  4.833664e+05  3.051158e+05  2.571373e+05  3.359410e+05  2.472485e+06
001-030               1.458227e+07  6.823509e+06  5.515140e+05  1.030555e+05  2.256574e+04  3.434073e+03           NaN
031-060               5.354744e+06  1.559842e+06  7.526119e+05  1.823889e+05  4.809148e+04  1.114667e+04  2.819162e+03
061-090               3.686390e+06  1.156526e+06  5.201652e+05  3.058760e+05  7.900538e+04  1.880027e+04  9.578257e+03
091-120               2.657608e+05  3.657604e+06  5.857510e+05  3.133471e+05  1.605200e+05  3.616268e+04  1.645157e+04
121-150               1.073101e+04  2.733105e+05  3.491127e+06  3.994037e+05  1.739123e+05  8.989068e+04  3.195684e+04
151+                  1.218273e+03  6.426295e+03  2.309793e+05  3.568203e+06  3.701976e+06  3.471941e+06  6.534511e+06

### Roll Rate on Unit Level

In [20]:
def rr_unit(df, ym, roll_group):
    l = []
    for i in range(len(ym)):
        if i== len(ym)-1:
            break
        else:
            dfs = rr(df,ym[i],ym[i+1])
            dfs['group'] = dfs['Delinquency_Bucket_x'] + ' to ' + dfs['Delinquency_Bucket_y']
            dfss = dfs[dfs['group'].isin(roll_group)].pivot_table(values = 'Unique_Order_ID',index = 'group',columns = 'Year_and_Month_y',aggfunc='nunique').rename_axis(None, axis=1)
            l.append(dfss)
    
    return l,pd.concat(l,axis = 1)

In [21]:
l,final_unit = rr_unit(RR, ym,roll_group)

201612 to 201701
201701 to 201702
201702 to 201703
201703 to 201704
201704 to 201705
201705 to 201706
201706 to 201707
201707 to 201708
201708 to 201709
201709 to 201710
201710 to 201711
201711 to 201712
201712 to 201801
201801 to 201802
201802 to 201803
201803 to 201804
201804 to 201805
201805 to 201806
201806 to 201807
201807 to 201808
201808 to 201809
201809 to 201810
201810 to 201811
201811 to 201812
201812 to 201901
201901 to 201902
201902 to 201903
201903 to 201904
201904 to 201905
201905 to 201906
201906 to 201907
201907 to 201908
201908 to 201909
201909 to 201910


In [23]:
l = []
for i in range(len(ym)):
    if i== len(ym)-20:
        break
    else:
        dfs = rr(RR,ym[i],ym[i+1])
        dfs['group'] = dfs['Delinquency_Bucket_x'] + ' to ' + dfs['Delinquency_Bucket_y']
        
        l.append(dfs)

201612 to 201701
201701 to 201702
201702 to 201703
201703 to 201704
201704 to 201705
201705 to 201706
201706 to 201707
201707 to 201708
201708 to 201709
201709 to 201710
201710 to 201711
201711 to 201712
201712 to 201801
201801 to 201802
201802 to 201803


In [24]:
l[0]['group'].value_counts(dropna = False)

000-000 to 000-000    368543
NaN                    76442
000-000 to 001-030     29410
151+ to 151+           14846
001-030 to 001-030     10488
001-030 to 000-000     10067
001-030 to 031-060      7112
031-060 to 061-090      6203
091-120 to 121-150      5550
061-090 to 091-120      5207
121-150 to 151+         4901
151+ to 000-000         3683
031-060 to 031-060      2212
031-060 to 000-000      1303
061-090 to 061-090      1300
000-000 to 031-060       999
091-120 to 091-120       802
031-060 to 001-030       536
121-150 to 121-150       519
061-090 to 000-000       413
001-030 to 061-090       336
091-120 to 151+          299
121-150 to 000-000       282
031-060 to 091-120       271
061-090 to 031-060       267
091-120 to 000-000       211
091-120 to 061-090       169
121-150 to 091-120        88
061-090 to 001-030        61
151+ to 121-150           58
061-090 to 121-150        38
091-120 to 031-060        28
000-000 to 061-090        24
121-150 to 061-090        15
001-030 to 091

In [32]:
l[0].groupby(['Delinquency_Bucket_x','Delinquency_Bucket_y']).size()#.reset_index()

Delinquency_Bucket_x  Delinquency_Bucket_y
000-000               000-000                 368543
                      001-030                  29410
                      031-060                    999
                      061-090                     24
                      091-120                      4
                      121-150                      5
                      151+                         7
001-030               000-000                  10067
                      001-030                  10488
                      031-060                   7112
                      061-090                    336
                      091-120                     11
                      121-150                      2
031-060               000-000                   1303
                      001-030                    536
                      031-060                   2212
                      061-090                   6203
                      091-120                    271
   

In [11]:
final_unit = rr_unit(RR, ym,roll_group)
final_unit.to_csv('rr_unit.csv')

201612.0 to 201701.0
201701.0 to 201702.0
201702.0 to 201703.0
201703.0 to 201704.0
201704.0 to 201705.0
201705.0 to 201706.0
201706.0 to 201707.0
201707.0 to 201708.0
201708.0 to 201709.0
201709.0 to 201710.0
201710.0 to 201711.0
201711.0 to 201712.0
201712.0 to 201801.0
201801.0 to 201802.0
201802.0 to 201803.0
201803.0 to 201804.0
201804.0 to 201805.0
201805.0 to 201806.0
201806.0 to 201807.0
201807.0 to 201808.0
201808.0 to 201809.0
201809.0 to 201810.0
201810.0 to 201811.0
201811.0 to 201812.0
201812.0 to 201901.0
201901.0 to 201902.0
201902.0 to 201903.0
201903.0 to 201904.0
201904.0 to 201905.0
201905.0 to 201906.0
201906.0 to 201907.0
201907.0 to 201908.0
201908.0 to 201909.0
201909.0 to 201910.0


In [ ]:
RR.pivot_table(values='Unique_Order_ID',index = 'Delinquency_Bucket',columns = 'Year_and_month',aggfunc='nunique').to_csv('total_unit.csv')

### Roll Rate on $Amount Level - `Current_Balance`

In [ ]:
def rr_amt(df, ym,roll_group):
    l = []
    for i in range(len(ym)):
        if i== len(ym)-1:
            break
        else:
            dfs = rr(df,ym[i],ym[i+1])
            dfs['group'] = dfs['Delinquency_Bucket_x'] + ' to ' + dfs['Delinquency_Bucket_y']
            dfss = dfs[dfs['group'].isin(roll_group)].pivot_table(values = 'Current_Balance_y',index = 'group',columns = 'Year_and_month_y',aggfunc='sum').rename_axis(None, axis=1)
            l.append(dfss)
    
    return pd.concat(l,axis = 1)

In [ ]:
final_amt = rr_amt(RR, ym,roll_group)
final_amt.to_csv('rr_amt.csv')

201612.0 to 201701.0
201701.0 to 201702.0
201702.0 to 201703.0


In [ ]:
RR.pivot_table(values='Current_Balance',index = 'Delinquency_Bucket',columns = 'Year_and_month',aggfunc='sum').to_csv('total_amt.csv')

### Use `Default_Status` as the DQ indicator

In [ ]:
roll_group_ds = ['Current to 001-030','001-030 to 031-060','031-060 to 061-090','061-090 to 091-120','091-120 to 121-150','121-150 to 151+']

### Roll Rate on Unit Level

In [ ]:
def rr_unit_ds(df, ym,roll_group):
    l = []
    for i in range(len(ym)):
        if i== len(ym)-1:
            break
        else:
            dfs = rr(df,ym[i],ym[i+1])
            dfs['group'] = dfs['Default_Status_x'] + ' to ' + dfs['Default_Status_y']
            dfss = dfs[dfs['group'].isin(roll_group)].pivot_table(values = 'Unique_Order_ID',index = 'group',columns = 'Year_and_month_y',aggfunc='nunique').rename_axis(None, axis=1)
#             dfs[dfs['group'].isin(g)]['group'].value_counts().reset_index()

            l.append(dfss)
    
    return pd.concat(l,axis = 1)

In [ ]:
unit_ds = rr_unit_ds(RR, ym,roll_group_ds)
unit_ds.to_csv("rr_unit_ds.csv")
RR.pivot_table(values='Unique_Order_ID',index = 'Default_Status',columns = 'Year_and_month',aggfunc='nunique').to_csv('total_unit_ds.csv')

### Roll Rate on $Amount Level - `Current_Balance`

In [ ]:
def rr_amt_ds(df, ym,roll_group):
    l = []
    for i in range(len(ym)):
        if i== len(ym)-1:
            break
        else:
            dfs = rr(df,ym[i],ym[i+1])
            dfs['group'] = dfs['Default_Status_x'] + ' to ' + dfs['Default_Status_y']
            dfss = dfs[dfs['group'].isin(roll_group)].pivot_table(values = 'Current_Balance_y',index = 'group',columns = 'Year_and_month_y',aggfunc='sum').rename_axis(None, axis=1)
            l.append(dfss)
    
    return pd.concat(l,axis = 1)

In [ ]:
amt_ds = rr_amt_ds(RR, ym,roll_group_ds)
amt_ds.to_csv('rr_amt_ds.csv')
RR.pivot_table(values='Current_Balance',index = 'Default_Status',columns = 'Year_and_month',aggfunc='sum').to_csv('total_amt_ds.csv')

### CO and DQ151+ by Channel/Industry/Company

In [ ]:
Perf.groupby(['YQ'])['Unique_Order_ID'].size().to_csv('./data/Unit_DQ.csv')
Perf.groupby(['YQ']).agg({'Current_Balance':'sum'}).to_csv('./data/Total_Balance_DQ.csv')
Perf.groupby(['YQ']).agg({'Losses':'sum'}).to_csv('./data/Total_Loss_CO.csv')

In [11]:
list(Perf)

['Unique_Order_ID',
 'Unique_Customer_ID',
 'Order_Amount',
 'Product_Markup',
 'Payments_Due',
 'Current_Balance',
 'Date_account_went_delinquent',
 'Default_Status',
 'Delinquency_Bucket',
 'Losses',
 'Auto_Pay_Enrollment',
 'Order_Closed_Flag',
 'Type_of_Backup_Payment',
 'Spending_Limit_at_time_of_Order',
 'Tenure_at_time_of_Order',
 'Salary_at_time_of_Order',
 'Street1_x',
 'Street2_x',
 'City_x',
 'State_x',
 'Zip_x',
 'items_ordered',
 'Year_and_Month',
 'EMPSTATUS',
 'Order_Date',
 'Unique_Company_ID',
 'Enrollment_Date',
 'Assigned_Spending_Limit',
 'Customer_Tenure',
 'Customer_Salary',
 'Prior_Customer_Flag',
 'Street1_y',
 'Street2_y',
 'City_y',
 'State_y',
 'Zip_y',
 'Status',
 'Term_Date',
 'Active',
 'Client ID',
 'Account Name',
 'Industry',
 'NAICS Code',
 'NAICS Description',
 'Broker',
 'TPA_x',
 'Launch Date',
 'Termination Date',
 'Affiliate/Fed Gov?',
 'Cash',
 'YQ']

In [70]:
Perf.pivot_table(values='Unique_Order_ID',index =  ['Affiliate/Fed Gov?','Delinquency_Bucket'],columns ='Year_and_Month',aggfunc='nunique')

Year_and_Month                         201201   201202   201203   201204   201205   201206   201207   201208   201209   201210   201211    201212    201301    201302    201303    201304    201305    201306    201307    201308    201309    201310    201311    201312    201401    201402    201403    201404    201405    201406    201407    201408    201409    201410    201411    201412    201501    201502    201503    201504    201505    201506    201507    201508    201509    201510    201511    201512    201601    201602    201603    201604    201605    201606    201607    201608    201609    201610    201611    201612    201701    201702    201703    201704    201705    201706    201707    201708    201709    201710    201711    201712    201801    201802    201803    201804    201805    201806    201807    201808    201809    201810    201811    201812    201901    201902    201903    201904    201905    201906    201907    201908    201909    201910
Affiliate/Fed Gov? Delinquency_Bucket                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                
Affiliate          000-000             5175.0  10688.0  16580.0  23058.0  28360.0  32152.0  39815.0  49003.0  55460.0  63344.0  81150.0  107633.0  114554.0  118889.0  115678.0  123329.0  126102.0  123322.0  129179.0  133765.0  131292.0  129667.0  135973.0  168969.0  159561.0  155419.0  150864.0  155048.0  153524.0  154873.0  157829.0  151932.0  157422.0  163292.0  171583.0  211181.0  180025.0  171361.0  185808.0  190994.0  182775.0  196223.0  202783.0  205484.0  212355.0  209885.0  244521.0  293161.0  268340.0  271384.0  279939.0  283773.0  278684.0  297182.0  288075.0  295579.0  296716.0  296532.0  336294.0  373420.0  327899.0  330814.0  342204.0  332751.0  333163.0  333289.0  342207.0  351983.0  356454.0  351790.0  405560.0  445339.0  417789.0  419701.0  410115.0  433630.0  436010.0  447884.0  450229.0  455047.0  442231.0  475170.0  524586.0  551684.0  508815.0  518305.0  481371.0  520568.0  523307.0  508751.0  518896.0  510796.0  512568.0  520818.0
                   001-030               14.0    215.0   1185.0   1739.0   2804.0   5086.0   5513.0   6095.0   8015.0   8279.0   8095.0   10133.0   12300.0   12396.0   19450.0   16087.0   16059.0   20199.0   17657.0   17321.0   18483.0   22077.0   25800.0   16529.0   15608.0   15063.0   15670.0   14318.0   16525.0   15070.0   14285.0   22804.0   19873.0   17841.0   24021.0   15605.0   29691.0   33520.0   22193.0   20605.0   29009.0   21517.0   20771.0   25201.0   22292.0   29205.0   19764.0   15698.0   26811.0   22156.0   20841.0   23572.0   32354.0   19796.0   29284.0   23694.0   24880.0   28588.0   24431.0   23269.0   34718.0   31069.0   25204.0   34085.0   38771.0   44095.0   38961.0   39827.0   35920.0   43085.0   35851.0   39818.0   35671.0   31862.0   48544.0   35848.0   37961.0   41980.0   38292.0   42668.0   58127.0   40918.0   41840.0   54291.0   62480.0   47565.0   80241.0   44413.0   40768.0   53354.0   38028.0   37424.0   40665.0   39175.0
                   031-060                NaN      4.0     27.0    130.0    239.0    499.0    644.0    891.0    927.0   1183.0   1459.0 

In [71]:
# Perf.pivot_table(values='Unique_Order_ID',index =  ['Affiliate/Fed Gov?','Delinquency_Bucket'],columns ='Year_and_Month',aggfunc='nunique').to_csv('./data/Channel_DQ.csv')

In [72]:
Perf.pivot_table(values='Unique_Order_ID',index =  ['Affiliate/Fed Gov?','Default_Status'],columns ='Year_and_Month',aggfunc='nunique')

Year_and_Month                     201201   201202   201203   201204   201205   201206   201207   201208   201209   201210   201211    201212    201301    201302    201303    201304    201305    201306    201307    201308    201309    201310    201311    201312    201401    201402    201403    201404    201405    201406    201407    201408    201409    201410    201411    201412    201501    201502    201503    201504    201505    201506    201507    201508    201509    201510    201511    201512    201601    201602    201603    201604    201605    201606    201607    201608    201609    201610    201611    201612    201701    201702    201703    201704    201705    201706    201707    201708    201709    201710    201711    201712    201801    201802    201803    201804    201805    201806    201807    201808    201809    201810    201811    201812    201901    201902    201903    201904    201905    201906    201907    201908    201909    201910
Affiliate/Fed Gov? Default_Status                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                
Affiliate          001-030           14.0    214.0   1181.0   1735.0   2796.0   5072.0   5498.0   6076.0   7995.0   8258.0   8076.0   10099.0   12256.0   12350.0   19389.0   16031.0   16009.0   20122.0   17593.0   17261.0   18410.0   21993.0   25700.0   16465.0   15560.0   15015.0   15622.0   14267.0   16474.0   15027.0   14234.0   22724.0   19804.0   17775.0   23942.0   15551.0   29574.0   33376.0   22104.0   20527.0   28891.0   21443.0   20689.0   25104.0   22220.0   29096.0   19703.0   15593.0   26639.0   21982.0   20680.0   23369.0   32134.0   19642.0   29062.0   23551.0   24737.0   28359.0   24216.0   23086.0   34481.0   30852.0   25001.0   33827.0   38504.0   43825.0   38738.0   39560.0   35650.0   42789.0   35543.0   39520.0   35408.0   31537.0   48159.0   35498.0   37622.0   41633.0   37892.0   42229.0   57589.0   40525.0   41409.0   53993.0   62020.0   47248.0   79836.0   44096.0   40420.0   52919.0   37709.0   36989.0   40296.0   38756.0
                   031-060            NaN      4.0     27.0    130.0    239.0    499.0    644.0    890.0    925.0   1182.0   1459.0    1907.0    1776.0    2173.0    2648.0    3414.0    3303.0    3537.0    3552.0    3691.0    4214.0    3731.0    3855.0    3838.0    3307.0    3284.0    3683.0    3687.0    3936.0    4083.0    4019.0    4500.0    4760.0    4394.0    4652.0    4433.0    4980.0    4997.0    5132.0    4745.0    6992.0    5228.0    4972.0    5528.0    5756.0    5706.0    5982.0    4987.0    5222.0    5171.0    5395.0    5874.0    7028.0    6330.0    7210.0    7206.0    7494.0    8137.0    7500.0    7939.0    7831.0    7068.0    7278.0    8033.0    9147.0    9576.0    9668.0    9409.0    9566.0   12369.0    9221.0    9878.0    8698.0    8845.0    9819.0   11783.0   10906.0   12548.0   13691.0   13263.0   13605.0   13468.0   12485.0   13261.0   11328.0   11394.0   13242.0   14139.0   12711.0   13447.0   13980.0   12862.0   13832.0   13684.0
                   061-090            NaN      NaN      3.0     18.0     89.0    181.0    375.0    426.0    600.0    624.0    852.0    1066.0    1176.0 

In [73]:
Perf.pivot_table(values='Unique_Order_ID',index =  ['Affiliate/Fed Gov?','Default_Status'],columns ='Year_and_Month',aggfunc='nunique').to_csv('./data/Channel_CO.csv')

In [16]:
def unit_analysis(df, index_list, file_name):
    dfs = df.pivot_table(values='Unique_Order_ID',index = index_list,columns ='YQ',aggfunc='count')
    dfs.to_csv('./data/{}.csv'.format(file_name))
    return dfs

In [17]:
Channel_DQ_unit = unit_analysis(Perf, ['Affiliate/Fed Gov?','Delinquency_Bucket'], 'Channel_DQ_unit')
Channel_CO_unit = unit_analysis(Perf, ['Affiliate/Fed Gov?','Default_Status'], 'Channel_CO_unit')

In [18]:
Industry_DQ = unit_analysis(Perf, ['Industry','Delinquency_Bucket'], 'Industry_DQ')
Industry_CO = unit_analysis(Perf, ['Industry','Default_Status'], 'Industry_CO')

In [19]:
Company_DQ = unit_analysis(Perf, ['Account Name','Delinquency_Bucket'], 'Company_DQ')
Company_CO = unit_analysis(Perf, ['Account Name','Default_Status'], 'Company_CO')

In [23]:
Industry_DQ

YQ                                                                    2012Q1   2012Q2   2012Q3    2012Q4    2013Q1    2013Q2    2013Q3    2013Q4    2014Q1    2014Q2    2014Q3    2014Q4    2015Q1    2015Q2    2015Q3    2015Q4    2016Q1    2016Q2    2016Q3    2016Q4    2017Q1    2017Q2    2017Q3    2017Q4    2018Q1    2018Q2    2018Q3    2018Q4    2019Q1    2019Q2    2019Q3    2019Q4
Industry                                         Delinquency_Bucket                                                                                                                                                                                                                                                                                                                             
Accommodation and Food Services                  000-000               834.0   2013.0   3206.0    5519.0    7203.0    7415.0    7940.0    9704.0   11334.0   11645.0   10970.0    9684.0    7556.0    7208.0    6882.0    8436.0    9025.0    9481.0    9847.0   11765.0    9571.0   10946.0   16775.0   29919.0   40610.0   53581.0   58406.0   72563.0   71724.0   77606.0   77764.0   27221.0
                                                 001-030                93.0    583.0   1078.0    1605.0    2545.0    3032.0    2623.0    2157.0    1242.0    1082.0     899.0    1790.0    1243.0     471.0     458.0     560.0     943.0    1036.0     918.0     851.0    2970.0    2100.0    2611.0    3242.0    5264.0    4592.0    9496.0   10004.0   15929.0   12273.0   10226.0    2845.0
                                                 031-060                 1.0     39.0    180.0     258.0     554.0     825.0     625.0     575.0     431.0     298.0     408.0     490.0     371.0     235.0     181.0     117.0     206.0     270.0     263.0     226.0     312.0     356.0     424.0     524.0     825.0    1338.0    2455.0    2157.0    2219.0    2668.0    2903.0     997.0
                                                 061-090                 NaN     10.0    109.0      86.0     125.0     242.0     456.0     276.0     235.0     223.0     325.0     316.0     256.0     166.0     123.0      97.0     128.0     193.0     192.0     174.0     172.0     288.0     273.0     304.0     546.0     914.0    1729.0    1749.0    1670.0    1870.0    2363.0     659.0
                                                 091-120                 NaN      6.0     44.0      72.0      82.0     107.0     352.0     222.0     196.0     186.0     236.0     192.0     224.0     164.0     102.0     109.0      69.0     149.0     177.0     152.0     152.0     200.0     247.0     243.0     442.0     688.0    1211.0    1570.0    1547.0    1564.0    2038.0     482.0
                                                 121-150                 NaN      NaN     20.0      41.0      73.0      97.0     183.0     211.0     171.0     144.0     182.0     171.0     181.0     142.0     120.0     119.0      82.0      96.0     177.0     130.0     133.0     185.0     250.0     215.0     307.0     518.0     941.0    1378.0    1657.0    1353.0    1753.0     603.0
                                                 151+                    NaN      NaN     14.0      59.0     162.0     198.0     324.0     519.0     453.0     405.0     434.0     376.0     442.0     467.0     395.0     294.0     304.0     214.0     353.0     530.0     411.0     514.0     780.0     783.0     972.0    1400.0    2580.0    3824.0    5936.0    6822.0    6239.0    2623.0
Administrative and Support                       000-000               196.0    594.0   1089.0    1852.0    2222.0    2218.0    2024.0    2299.0    3063.0    3384.0    4177.0    5615.0    5960.0    6595.0    7771.0    9577.0   10041.0   11205.0   11766.0   14615.0   15508.0   16202.0   17844.0   20785.0   19469.0   20590.0   22793.0   22218.0   24291.0   25042.0   24881.0    8675.0
                                                 001-030                17.0     49.0    170.0     158.0     451.0     510.0     439.0     435.0     5

In [11]:
# Perf.groupby(['Year_and_Month'])['Unique_Order_ID'].size().to_csv('./data/Unit_DQ.csv')

In [14]:
# Perf.groupby(['Year_and_Month']).agg({'Current_Balance':'sum'}).to_csv('./data/Total_Balance_DQ.csv')

In [15]:
# Perf.groupby(['Year_and_Month']).agg({'Losses':'sum'}).to_csv('./data/Total_Loss_CO.csv')

In [20]:
def dollar_analysis(df, index_list,balance_ind, file_name):
    dfs = df.pivot_table(values=balance_ind,index = index_list,columns ='YQ',aggfunc='sum')
    dfs.to_csv('./data/{}.csv'.format(file_name))
    return dfs

In [13]:
Channel_DQ_Dollar = dollar_analysis(Perf,['Affiliate/Fed Gov?','Delinquency_Bucket'],'Current_Balance','Channel_DQ_Dollar')
Channel_CO_Dollar = dollar_analysis(Perf,['Affiliate/Fed Gov?','Default_Status'],'Losses','Channel_CO_Dollar')

In [14]:
Channel_DQ_Dollar

YQ                                          2012Q1       2012Q2        2012Q3        2012Q4        2013Q1        2013Q2        2013Q3        2013Q4        2014Q1        2014Q2        2014Q3        2014Q4        2015Q1        2015Q2        2015Q3        2015Q4        2016Q1        2016Q2        2016Q3        2016Q4        2017Q1        2017Q2        2017Q3        2017Q4        2018Q1        2018Q2        2018Q3        2018Q4        2019Q1        2019Q2        2019Q3        2019Q4
Affiliate/Fed Gov? Delinquency_Bucket                                                                                                                                                                                                                                                                                                                                                                                                                                                              
Affiliate          000-000             37987387.69  86354955.80  1.307797e+08  2.063443e+08  2.447578e+08  2.252656e+08  2.123638e+08  2.446943e+08  2.822851e+08  2.499656e+08  2.338458e+08  2.876513e+08  3.051807e+08  2.868719e+08  2.889104e+08  3.626807e+08  4.091091e+08  3.665051e+08  3.469918e+08  4.205410e+08  4.595876e+08  4.151438e+08  4.075594e+08  4.896565e+08  5.445082e+08  5.120861e+08  4.896872e+08  5.799357e+08  5.890017e+08  5.407071e+08  5.199484e+08  1.701964e+08
                   001-030              1583478.29   9756162.83  1.718374e+07  1.991023e+07  2.976055e+07  3.097277e+07  2.745780e+07  3.229276e+07  2.760297e+07  2.396212e+07  2.777467e+07  2.826546e+07  5.300476e+07  3.656360e+07  3.186554e+07  2.929739e+07  3.945163e+07  3.415546e+07  3.068738e+07  3.065723e+07  4.656491e+07  5.116220e+07  4.305444e+07  4.389128e+07  5.377316e+07  4.671449e+07  5.255139e+07  5.007450e+07  7.583373e+07  5.168473e+07  3.878758e+07  1.217312e+07
                   031-060                35713.32    958924.36  2.283890e+06  3.570780e+06  4.433351e+06  5.975270e+06  6.002086e+06  5.481827e+06  5.372624e+06  6.381568e+06  6.442652e+06  6.088482e+06  8.281872e+06  8.820326e+06  7.619956e+06  7.454882e+06  8.097296e+06  9.267026e+06  9.246761e+06  9.253244e+06  1.046267e+07  1.211682e+07  1.165431e+07  1.189454e+07  1.259728e+07  1.511671e+07  1.597349e+07  1.441656e+07  1.451645e+07  1.593782e+07  1.463637e+07  4.657102e+06
                   061-090                 2330.50    309010.98  1.424580e+06  2.102088e+06  2.705645e+06  3.777717e+06  4.201225e+06  4.168484e+06  3.656000e+06  4.668047e+06  5.009701e+06  4.726546e+06  4.513565e+06  6.083111e+06  5.649805e+06  6.006251e+06  5.634323e+06  7.089138e+06  7.487721e+06  7.204506e+06  7.133666e+06  9.200642e+06  9.222420e+06  8.881968e+06  8.738860e+06  1.091668e+07  1.197071e+07  1.219614e+07  1.100321e+07  1.277878e+07  1.146419e+07  3.806575e+06
                   091-120                     NaN    106616.04  8.590771e+05  1.565433e+06  2.223768e+06  2.798517e+06  3.475575e+06  3.626244e+06  3.096109e+06  3.711755e+06  4.043951e+06  4.100509e+06  3.844191e+06  4.760363e+06  5.080394e+06  5.198384e+06  4.810848e+06  5.715492e+06  6.488063e+06  6.457636e+06  6.288095e+06  7.102507e+06  8.270647e+06  7.904465e+06  7.802350e+06  8.870730e+06  1.006814e+07  1.074680e+07  9.736777e+06  1.151362e+07  1.054437e+07  3.210405e+06
                   121-150                     NaN     18017.93  5.668070e+05  1.167201e+06  1.917722e+06  2.236165e+06  3.059025e+06  3.267166e+06  3.160415e+06  3.116314e+06  3.874464e+06  3.655206e+06  3.573691e+06  3.930382e+06  4.637821e+06  4.831721e+06  4.784461e+06  4.723836e+06  5.525910e+06  5.928710e+06  5.846670e+06  6.084036e+06  7.675457e+06  7.676652e+06  7.243503e+06  7.473948e+06  9.227582e+06  9.953739e+06  9.806469e+06  1.003874e+07  1.018861e+07  3.026762e+06
                   151+                        NaN      2330.50  2.658417e+05  1.732694e+06  4.605473e+06  5.352068e+06  7.48166

In [21]:
Industry_DQ_Dollar = dollar_analysis(Perf, ['Industry','Delinquency_Bucket'],'Current_Balance', 'Industry_DQ_Dollar')
Industry_CO_Dollar = dollar_analysis(Perf, ['Industry','Default_Status'],'Losses', 'Industry_CO_Dollar')

In [22]:
Company_DQ_Dollar = dollar_analysis(Perf, ['Account Name','Delinquency_Bucket'], 'Current_Balance','Company_DQ_Dollar')
Company_CO_Dollar = dollar_analysis(Perf, ['Account Name','Default_Status'],'Losses', 'Company_CO_Dollar')

In [11]:
Perf.pivot_table(values='Unique_Order_ID',index = 'Affiliate/Fed Gov?',columns ='YQ',aggfunc='count')

YQ                  2012Q1  2012Q2  2012Q3  2012Q4  2013Q1  2013Q2  2013Q3  2013Q4  2014Q1  2014Q2  2014Q3  2014Q4  2015Q1  2015Q2  2015Q3  2015Q4  2016Q1   2016Q2   2016Q3   2016Q4   2017Q1   2017Q2   2017Q3   2017Q4   2018Q1   2018Q2   2018Q3   2018Q4   2019Q1   2019Q2   2019Q3  2019Q4
Affiliate/Fed Gov?                                                                                                                                                                                                                                                                              
Affiliate            33894   94481  169380  290512  414209  455860  489042  545619  557661  555864  578614  659774  681208  702911  756204  888431  972458  1023004  1058701  1198151  1207385  1244941  1316043  1486486  1536029  1611372  1688054  1910402  1931325  1916584  1902121  646896
Fed Gov              14201   43097   75403  120551  162328  167524  170812  178149  186808  184293  187775  192425  197048  198293  201679  209919  228629   233764   232558   253022   241783   244696   249197   269475   259109   256115   255212   267947   264144   258710   251043   82988

In [12]:
Perf.pivot_table(values='Unique_Order_ID',index = 'Affiliate/Fed Gov?',columns ='YQ',aggfunc='count').to_csv('./data/channel_vol.csv')

In [24]:
Perf[Perf['Order_Amount']!=0].pivot_table(values='Order_Amount',index = 'Affiliate/Fed Gov?',columns ='YQ',aggfunc='sum').to_csv('./data/channel_vol_dollar.csv')

In [10]:
Perf.loc[Perf['Order_Amount']=='.','Order_Amount']=0

In [23]:
Perf[Perf['Order_Amount']!=0].pivot_table(values='Order_Amount',index = 'Affiliate/Fed Gov?',columns ='YQ',aggfunc='sum')

YQ                        2012Q1        2012Q2        2012Q3        2012Q4        2013Q1        2013Q2        2013Q3        2013Q4        2014Q1        2014Q2        2014Q3        2014Q4        2015Q1        2015Q2        2015Q3        2015Q4        2016Q1        2016Q2        2016Q3        2016Q4        2017Q1        2017Q2        2017Q3        2017Q4        2018Q1        2018Q2        2018Q3        2018Q4        2019Q1        2019Q2        2019Q3        2019Q4
Affiliate/Fed Gov?                                                                                                                                                                                                                                                                                                                                                                                                                                                                
Affiliate           4.164950e+07  1.142972e+08  2.020051e+08  3.390581e+08  4.697782e+08  5.105603e+08  5.435597e+08  5.970654e+08  5.983950e+08  5.883430e+08  6.036916e+08  6.723369e+08  6.767201e+08  6.868910e+08  7.220616e+08  8.176080e+08  8.574257e+08  8.806255e+08  8.970111e+08  1.000822e+09  9.890866e+08  1.019687e+09  1.079636e+09  1.214233e+09  1.225629e+09  1.262102e+09  1.294571e+09  1.429540e+09  1.404171e+09  1.384362e+09  1.371757e+09  4.656834e+08
Fed Gov             2.073748e+07  6.272178e+07  1.097014e+08  1.769356e+08  2.357009e+08  2.413198e+08  2.442904e+08  2.513925e+08  2.560002e+08  2.514817e+08  2.563951e+08  2.634690e+08  2.666492e+08  2.677864e+08  2.716016e+08  2.796060e+08  2.954790e+08  2.986665e+08  2.951381e+08  3.164033e+08  2.964619e+08  2.987079e+08  3.044240e+08  3.293614e+08  3.162421e+08  3.124658e+08  3.097003e+08  3.236583e+08  3.145911e+08  3.087751e+08  3.010571e+08  9.961710e+07

In [11]:
Perf['Order_Amount'] = Perf['Order_Amount'].astype(float)

In [19]:
Perf[Perf['Order_Amount']=='.']['Unique_Order_ID'].unique()

array([10301220, 10855576, 11070752, 11157107, 11268048, 11296032,
       11378495, 11447427, 11450524, 11651222, 11686816, 11705544,
       11803362, 11917580, 11921266, 11969921, 11972081, 12075416,
       12391160, 12403301, 12412398, 12682243, 12992647, 13015562,
       13069677, 13128521, 13525553, 13795970, 13938014, 14110591,
       14600898, 14787422, 15012173, 15033030, 15311668, 15386177,
       15877279, 16093308, 16145148, 16173023, 16182131, 16182169,
       16288201, 17263585, 18065037, 19507564, 19655790, 19684389,
       19703482, 19706498, 19722813, 19723584, 19723598, 19723628,
       19724789, 19725931, 19755075, 19795416, 19795522, 19841356,
       20107928, 21087221, 22923144, 23965260, 24386489, 24944095,
       25724397, 'AFGWRIG947048', 'AFGWRIG959153', 'BANWILS1106544',
       'BANWILS929205', 'COMBROO1440708', 'COMBROO1472551',
       'GOVMCCL1063858', 'GOVMCCL1241849', 'LEEFORR944916',
       'SIAMURP1098873', 'SIAMURP1102320', 'SIAMURP1377007',
       'SIAMU

In [20]:
list(Perf)

['Unique_Order_ID',
 'Unique_Customer_ID',
 'Order_Amount',
 'Product_Markup',
 'Payments_Due',
 'Current_Balance',
 'Date_account_went_delinquent',
 'Default_Status',
 'Delinquency_Bucket',
 'Losses',
 'Auto_Pay_Enrollment',
 'Order_Closed_Flag',
 'Type_of_Backup_Payment',
 'Spending_Limit_at_time_of_Order',
 'Tenure_at_time_of_Order',
 'Salary_at_time_of_Order',
 'Street1_x',
 'Street2_x',
 'City_x',
 'State_x',
 'Zip_x',
 'items_ordered',
 'Year_and_Month',
 'EMPSTATUS',
 'Order_Date',
 'Unique_Company_ID',
 'Enrollment_Date',
 'Assigned_Spending_Limit',
 'Customer_Tenure',
 'Customer_Salary',
 'Prior_Customer_Flag',
 'Street1_y',
 'Street2_y',
 'City_y',
 'State_y',
 'Zip_y',
 'Status',
 'Term_Date',
 'Active_x',
 'Client ID_x',
 'Account Name_x',
 'Industry_x',
 'NAICS Code_x',
 'NAICS Description_x',
 'Broker_x',
 'TPA_x_x',
 'Launch Date_x',
 'Termination Date_x',
 'Affiliate/Fed Gov?_x',
 'Cash_x',
 'Active_y',
 'Client ID_y',
 'Account Name_y',
 'Current Eligibles',
 'Eligible

In [21]:
Perf[Perf['Client ID_x'].isin([2049,2302,2311,2250,2496,2422])].pivot_table(values = 'Unique_Customer_ID',index = 'Account Name_x',columns = 'YQ',aggfunc='count')

YQ                                                  2012Q1  2012Q2  2012Q3  2012Q4  2013Q1  2013Q2  2013Q3  2013Q4  2014Q1  2014Q2  2014Q3  2014Q4  2015Q1  2015Q2  2015Q3  2015Q4  2016Q1  2016Q2  2016Q3  2016Q4  2017Q1  2017Q2  2017Q3  2017Q4  2018Q1  2018Q2  2018Q3  2018Q4  2019Q1  2019Q2  2019Q3  2019Q4
Account Name_x                                                                                                                                                                                                                                                                                                    
CHARTER COMMUNICATIONS                                   4      17    1313   10143   17727   22042   26469   29458   29681   31235   34124   39592   40450   42654   46513   54120   57995   61005   63619   69731   68839   72208   75895   83619   86234   90713   94065  114322  108187   87339   63970   17216
COMMUNITY HEALTH SYSTEMS                               306     844    1548    2786    3973    4255    4449    4776    5106    5440    5804    6994    6225    5355    4281    8809   15512   18085   22005   32008   34514   37175   40857   46556   47326   48722   50394   55333   52405   50411   48865   16187
COMPASS GROUP (NEW)                                      2      10      33      48      77      98     105     125     141     130     117     122      94      78      81      73      74      71      65      71      62      68    5704   17683   31355   42651   53212   64552   69320   71189   70049   23988
DAVITA INC                                            1399    4071    7412   12091   15961   17068   17796   18722   18027   17784   17703   19029   19141   22317   26226   33106   41146   45020   47998   52920   52175   53048   55673   59739   60142   61424   62089   66981   66605   65515   63510   21303
FEDERAL GOVERNMENT/POSTAL WORKERS/NIH/DEPT OF E...   10998   33222   58078   93393  126386  130070  132643  138903  146777  145967  149473  153367  158106  159753  162887  169638  185851  190773  190181  207267  198087  200136  203431  220061  211703  209676  209177  218915  216510  211350  204696   67494
THE HOME DEPOT                                          16      29      52    2887   15127   23007   30725   42099   47464   48392   52520   61818   63668   66662   72716   83875   90074   94001   95957  105301  102964  104636  108555  118753  119477  124135  126929  142160  143777  145636  144842   50045

In [29]:
Perf['EMPSTATUS'] =Perf['EMPSTATUS'].apply(lambda x:x.lower() if pd.notnull(x) else '') 

In [28]:
Perf['EMPSTATUS'].value_counts(dropna = False)

Employed       35269671
Terminated      2564889
Direct Bill      691406
LOA              448349
Deceased           7095
NaN                 699
DedStop             131
DECEASED             33
Active                8
Name: EMPSTATUS, dtype: int64

In [30]:
Perf[Perf['Delinquency_Bucket']=='151+'].pivot_table(values = 'Unique_Customer_ID' ,index = 'YQ',columns = 'EMPSTATUS',aggfunc='count',margins=True)

EMPSTATUS  deceased  dedstop  direct bill  employed      loa  terminated      All
YQ                                                                               
2012Q2          NaN      NaN          NaN       NaN      NaN         3.0        3
2012Q3          NaN      NaN         56.0     163.0     23.0       141.0      383
2012Q4          2.0      NaN        430.0     830.0    117.0      1057.0     2436
2013Q1          4.0      NaN       1389.0    2407.0    251.0      3393.0     7444
2013Q2          7.0      NaN       2307.0    3301.0    332.0      3911.0     9858
2013Q3         21.0      NaN       3524.0    5919.0    545.0      6138.0    16147
2013Q4         20.0      NaN       2653.0    9337.0    583.0      7252.0    19845
2014Q1         12.0      1.0       1515.0   12751.0    737.0      7276.0    22292
2014Q2         16.0      8.0       1902.0   13646.0    649.0      5987.0    22208
2014Q3         20.0     20.0       2150.0   13796.0    772.0      8022.0    24780
2014Q4         26.0     10.0       1906.0   12435.0    752.0      9097.0    24226
2015Q1         12.0      6.0       1815.0   13862.0    781.0     10247.0    26723
2015Q2         25.0      6.0       1593.0   14515.0    858.0      9527.0    26524
2015Q3         17.0      2.0       2167.0   14903.0   1227.0     11026.0    29342
2015Q4         32.0      NaN       2439.0   15542.0   1511.0     14299.0    33823
2016Q1         43.0      NaN       2768.0   19769.0   1576.0     21105.0    45261
2016Q2         64.0      NaN       2743.0   20151.0   1572.0     20486.0    45016
2016Q3        142.0      NaN       2540.0   22725.0   1844.0     19699.0    46950
2016Q4         13.0      NaN       6185.0   22766.0   2213.0     24982.0    56159
2017Q1         25.0      NaN       9259.0   18409.0   1930.0     27365.0    56988
2017Q2         39.0      NaN      10410.0   19377.0   2027.0     33805.0    65658
2017Q3         80.0      NaN       8345.0   22318.0   2388.0     40792.0    73923
2017Q4         56.0      NaN       9194.0   25939.0   2491.0     47366.0    85046
2018Q1         50.0      NaN      10613.0   29409.0   2621.0     58156.0   100849
2018Q2         31.0      NaN       7102.0   29368.0   2312.0     56384.0    95197
2018Q3         27.0      NaN      46080.0   28826.0   2105.0     17977.0    95015
2018Q4         15.0      NaN      69728.0   34800.0   2723.0      3536.0   110802
2019Q1          7.0      NaN      55068.0   40792.0   3445.0     28040.0   127352
2019Q2         31.0      NaN      15024.0   37367.0   3670.0     56217.0   112309
2019Q3          8.0      NaN      11193.0   44813.0   5153.0     69018.0   130185
2019Q4          4.0      NaN       3578.0   17943.0   2006.0     27027.0    50558
All           849.0     53.0     295676.0  568179.0  49214.0    649331.0  1563302

In [31]:
Perf[Perf['Delinquency_Bucket']=='151+'].pivot_table(values = 'Unique_Customer_ID' ,index = 'YQ',columns = 'EMPSTATUS',aggfunc='count',margins=True).to_csv('./data/EMPSTATUS.csv')

In [32]:
Perf.head()

Unique_Order_ID  Unique_Customer_ID Order_Amount Product_Markup Payments_Due  Current_Balance Date_account_went_delinquent Default_Status Delinquency_Bucket  Losses Auto_Pay_Enrollment Order_Closed_Flag Type_of_Backup_Payment Spending_Limit_at_time_of_Order Tenure_at_time_of_Order Salary_at_time_of_Order        Street1_x Street2_x      City_x State_x    Zip_x                                      items_ordered Year_and_Month EMPSTATUS  Order_Date  Unique_Company_ID Enrollment_Date  Assigned_Spending_Limit  Customer_Tenure  Customer_Salary Prior_Customer_Flag        Street1_y Street2_y      City_y State_y  Zip_y    Status Term_Date Active_x  Client ID_x                                     Account Name_x                       Industry_x  NAICS Code_x NAICS Description_x Broker_x TPA_x_x Launch Date_x Termination Date_x Affiliate/Fed Gov?_x Cash_x Active_y  Client ID_y                                     Account Name_y  Current Eligibles  Eligibles at time of Launch  \
0        10000091           100486182      1072.88              .        40.11           907.86                            .        Current            000-000     0.0                  PA                 N                    ACH                            96.6                     327                  800.29  929 IMPERIAL CT       NaN  HALETHORPE      MD  21227.0  DeWalt 12in 15-Amp Double-Bevel Compound Miter...     2014-04-01  employed  03/15/2014             2049.0      02/25/2014                   9660.0            327.0          80029.0        Repeat Buyer  929 IMPERIAL CT       NaN  HALETHORPE      MD  21227  Employed       NaN        Y       2049.0  FEDERAL GOVERNMENT/POSTAL WORKERS/NIH/DEPT OF ...  Federal Government/Associations           NaN                 NaN      NaN     NaN    2002-07-01                NaT              Fed Gov    NaN        Y       2049.0  FEDERAL GOVERNMENT/POSTAL WORKERS/NIH/DEPT OF ...                NaN                    2900000.0   
1        10000091           100486182      1072.88              .        40.11           817.86                            .        Current            000-000     0.0                  PA                 N                    ACH                            96.6                     327                  800.29  929 IMPERIAL CT       NaN  HALETHORPE      MD  21227.0  DeWalt 12in 15-Amp Double-Bevel Compound Miter...     2014-05-01  employed  03/15/2014             2049.0      02/25/2014                   9660.0            327.0          80029.0        Repeat Buyer  929 IMPERIAL CT       NaN  HALETHORPE      MD  21227  Employed       NaN        Y       2049.0  FEDERAL GOVERNMENT/POSTAL WORKERS/NIH/DEPT OF ...  Federal Government/Associations           NaN                 NaN      NaN     NaN    2002-07-01                NaT              Fed Gov    NaN        Y       2049.0  FEDERAL GOVERNMENT/POSTAL WORKERS/NIH/DEPT OF ...                NaN                    2900000.0   
2        10000091           100486182      1072.88              .        40.11           727.86                            .        Current            000-000     0.0                  PA                 N                    ACH                            96.6                     327                  800.29  929 IMPERIAL CT       NaN  HALETHORPE      MD  21227.0  DeWalt 12in 15-Amp Double-Bevel Compound Miter...     2014-06-01  employed  03/15/2014             2049.0      02/25/2014                   9660.0            327.0          80029.0        Repeat Buyer  929 IMPERIAL CT       NaN  HALETHORPE      MD  21227  Employed       NaN        Y       2049.0  FEDERAL GOVERNMENT/POSTAL WORKERS/NIH/DEPT OF ...  Federal Government/Associations           NaN                 NaN      NaN     NaN    2002-07-01                NaT              Fed Gov    NaN        Y       2049.0  FEDERAL GOVERNMENT/POSTAL WORKERS/NIH/DEPT OF ...                NaN                    2900000.0   
3        10000091           100486182      1072.88              .        4

In [33]:
Client.head()

Active  Client ID                    Account Name  Current Eligibles  Eligibles at time of Launch                                       Industry  NAICS Code                                  NAICS Description                               Broker TPA_x Launch Date Termination Date Affiliate/Fed Gov?  HOST ID CLIENT CODE                     CLIENT NAME         CLIENT AR TPA_y                                Cash
0      Y       7601                           Aetna                NaN                          NaN              Health Care and Social Assistance         NaN                                                NaN                                  NaN   NaN  2017-10-13              NaT          Affiliate      NaN         NaN                             NaN               NaN   NaN                                 NaN
1      Y       1500                      PPC SELECT                NaN                          NaN  Other Services (except Public Administration)         NaN                                                NaN                                  NaN   NaN         NaT              NaT                NaN      NaN         NaN                             NaN               NaN   NaN                                 NaN
2      Y       4270       ATLANTIC GENERAL HOSPITAL              418.0                        418.0              Health Care and Social Assistance    622110.0             General Medical and Surgical Hospitals  Maryland Hospital Association/PRIME   NaN  2006-03-01              NaT          Affiliate      NaN         NaN                             NaN               NaN   NaN                                 NaN
3      Y       1000  SOCIAL SECURITY ADMINISTRATION            60000.0                      70000.0                Federal Government/Associations    923130.0  Administration of Social, Human Resource and I...                                  PPC   EAA  2002-07-01              NaT            Fed Gov   1000.0         SSA  SOCIAL SECURITY ADMINISTRATION  KELLY MENCHINGER   EAA  TPA sends cash on behalf of client
4      Y       3900                   STEPHENS, INC             1000.0                       1000.0                          Finance and Insurance    523110.0          Investment Banking and Securities Dealing                                  PPC   NaN  2002-02-01              NaT          Affiliate      NaN         NaN                             NaN               NaN   NaN                                 NaN

In [34]:
list(Client)

['Active',
 'Client ID',
 'Account Name',
 'Current Eligibles',
 'Eligibles at time of Launch',
 'Industry',
 'NAICS Code',
 'NAICS Description',
 'Broker',
 'TPA_x',
 'Launch Date',
 'Termination Date',
 'Affiliate/Fed Gov?',
 'HOST ID',
 'CLIENT CODE',
 'CLIENT NAME',
 'CLIENT AR',
 'TPA_y',
 'Cash']

In [37]:
Client.sort_values(by=['Current Eligibles'],ascending=False)

Active  Client ID                                       Account Name  Current Eligibles  Eligibles at time of Launch                                          Industry  NAICS Code                                  NAICS Description                                             Broker                                              TPA_x Launch Date Termination Date Affiliate/Fed Gov?  HOST ID CLIENT CODE                                        CLIENT NAME         CLIENT AR                      TPA_y                                Cash
98              Y       9991        NYSUT- NEW YORK STATE UNITED TEACHERS (NYW)           674049.0                          NaN                              Educational Services    813930.0       Labor Unions and Similar Labor Organizations                                                NaN                                                NaN  2017-11-20              NaT          Affiliate      NaN         NaN                                                NaN               NaN                        NaN                                 NaN
442    Terminated       5004                  NURSES SERVICE ORGANIZATION (NSO)           433512.0                     433512.0  Professional, Scientific, and Technical Services    621399.0  Offices of All Other Miscellaneous Health Prac...  Perks Group / Augeo Affinity Insurance Service...                                                NaN  2015-04-09       2017-02-18          Affiliate      NaN         NaN                                                NaN               NaN                        NaN                                 NaN
80              Y       2499                NEW YORK STATE UNITED TEACHERS (PD)           346619.0                     575000.0                              Educational Services    813930.0       Labor Unions and Similar Labor Organizations                                                NaN                                                NaN  2017-11-20              NaT          Affiliate   2499.0         NYS             NEW YORK STATE UNITED TEACHERS (NYSUT)  KELLY MENCHINGER                      NYSUT  TPA sends cash on behalf of client
95              Y       5008               NEW YORK STATE UNITED TEACHERS (ACH)           327232.0                     200000.0                     State Government/Associations    813930.0       Labor Unions and Similar Labor Organizations                                                NaN                                                NaN  2017-11-20              NaT          Affiliate      NaN         NaN                                                NaN               NaN                        NaN                                 NaN
7               Y       2047        AMERICAN FEDERATION OF GOVERNMENT EMPLOYEES           308000.0                     272495.0                   Federal Government/Associations    813930.0       Labor Unions and Similar Labor Organizations                                                PPC                                                NaN  2003-04-03              NaT            Fed Gov      NaN         NaN                                                NaN               NaN                        NaN                                 NaN
186             Y       2302                                     THE HOME DEPOT           296526.0                     200584.0                                      Retail Trade    444110.0                                       Home Centers                                                NaN                                   Alight Solutions  2012-11-20              NaT          Affiliate   2302.0         THD                                     THE HOME DEPOT     DENA THOMPSON                 AON HEWITT                   Client sends cash
112             Y       9990                            CSEA LOCAL 1000 - (CNA)           249816.0                          NaN                     Local Government/Associations    813930.0       Labor U

In [38]:
Client.sort_values(by=['Eligibles at time of Launch'],ascending=False)

Active  Client ID                                       Account Name  Current Eligibles  Eligibles at time of Launch                                          Industry  NAICS Code                                  NAICS Description                                             Broker                                              TPA_x Launch Date Termination Date Affiliate/Fed Gov?  HOST ID CLIENT CODE                                        CLIENT NAME         CLIENT AR                      TPA_y                                Cash
8               Y       2049  FEDERAL GOVERNMENT/POSTAL WORKERS/NIH/DEPT OF ...                NaN                    2900000.0                   Federal Government/Associations         NaN                                                NaN                                                NaN                                                NaN  2002-07-01              NaT            Fed Gov      NaN         NaN                                                NaN               NaN                        NaN                                 NaN
80              Y       2499                NEW YORK STATE UNITED TEACHERS (PD)           346619.0                     575000.0                              Educational Services    813930.0       Labor Unions and Similar Labor Organizations                                                NaN                                                NaN  2017-11-20              NaT          Affiliate   2499.0         NYS             NEW YORK STATE UNITED TEACHERS (NYSUT)  KELLY MENCHINGER                      NYSUT  TPA sends cash on behalf of client
442    Terminated       5004                  NURSES SERVICE ORGANIZATION (NSO)           433512.0                     433512.0  Professional, Scientific, and Technical Services    621399.0  Offices of All Other Miscellaneous Health Prac...  Perks Group / Augeo Affinity Insurance Service...                                                NaN  2015-04-09       2017-02-18          Affiliate      NaN         NaN                                                NaN               NaN                        NaN                                 NaN
7               Y       2047        AMERICAN FEDERATION OF GOVERNMENT EMPLOYEES           308000.0                     272495.0                   Federal Government/Associations    813930.0       Labor Unions and Similar Labor Organizations                                                PPC                                                NaN  2003-04-03              NaT            Fed Gov      NaN         NaN                                                NaN               NaN                        NaN                                 NaN
124             Y       2475  NATIONAL ACTIVE AND RETIRED FEDERAL EMPLOYEES ...           230000.0                     230000.0                   Federal Government/Associations    813319.0                Other Social Advocacy Organizations                                                NaN                                                NaN  2016-11-15              NaT            Fed Gov      NaN         NaN                                                NaN               NaN                        NaN                                 NaN
186             Y       2302                                     THE HOME DEPOT           296526.0                     200584.0                                      Retail Trade    444110.0                                       Home Centers                                                NaN                                   Alight Solutions  2012-11-20              NaT          Affiliate   2302.0         THD                                     THE HOME DEPOT     DENA THOMPSON                 AON HEWITT                   Client sends cash
5               Y       2458                       FEDERAL MANAGERS ASSOCIATION           200000.0                     200000.0                   Federal Government/Associations    813920.0              

In [10]:
2900000/346619

8.366535013949033

In [22]:
Perf.pivot_table(values='Unique_Order_ID',index = 'YQ',columns ='Industry',aggfunc='count').to_csv('./data/Industry_vol.csv')

In [28]:
Perf.pivot_table(values='Order_Amount',index = 'YQ',columns ='Industry',aggfunc=['sum','mean'])

sum                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               mean                                                                                                                                                                                                                                                                \
Industry Accommodation and Food Services Administrative and Support Arts, Entertainment, and Recreation Construction Educational Services Engineering Federal Government/Associations Finance and Insurance Health Care and Social Assistance Healthcare   Information Local Government/Associations Machinery Management of Companies and Enterprises Manufacturing Mining, Quarrying, and Oil and Gas Extraction Nursing and Residential Care Facilities Other Services (except Public Administration) Professional, Scientific, and Technical Services Real Estate and Rental and Leasing Retail & Wholesale Trade  Retail Trade State Government/Associations Transportation and Warehousing  Utilities Wholesale Trade Accommodation and Food Services Administrative and Support Arts, Entertainment, and Recreation Construction Educational Services  Engineering Federal Government/Associations Finance and Insurance Health Care and Social Assistance   Healthcare  Information Local Government/Associations   
YQ                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                          
2012Q1                      1.181998e+06                  265866.88                                 NaN          NaN            430182.99         NaN                    2.073748e+07          8.018454e+05                      1.589097e+07        NaN  2.117687e+06                  8.146663e+05       NaN                                32116.35  2.926118e+06                                           NaN                            2.572650e+06                                  1.319371e+06                                        329944.63                           40426.74                      NaN  4.613256e+06                  7.046611e+06                   1.972582e+06    9398.04       240010.24                     1273.704397                1236.590140                                 NaN          NaN          1059.564015          NaN                     1460.282732           1203.972057                       1293.000087          NaN  1290.485704                   1441.887327   
2012Q2                      3.272614e+06                  824023.62              

In [20]:
Perf[Perf['Delinquency_Bucket']=='151+'].pivot_table(values='Unique_Order_ID',index = 'YQ',columns ='Industry',aggfunc='count')

Industry  Accommodation and Food Services  Administrative and Support  Arts, Entertainment, and Recreation  Construction  Educational Services  Federal Government/Associations  Finance and Insurance  Health Care and Social Assistance  Information  Local Government/Associations  Management of Companies and Enterprises  Manufacturing  Mining, Quarrying, and Oil and Gas Extraction  Nursing and Residential Care Facilities  Other Services (except Public Administration)  Professional, Scientific, and Technical Services  Real Estate and Rental and Leasing  Retail & Wholesale Trade  Retail Trade  State Government/Associations  Transportation and Warehousing  Utilities  Wholesale Trade
YQ                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           
2012Q2                                NaN                         NaN                                  NaN           NaN                   NaN                              NaN                    NaN                                NaN          NaN                            NaN                                      NaN            1.0                                            NaN                                      NaN                                            NaN                                               NaN                                 NaN                       NaN           2.0                            NaN                             NaN        NaN              NaN
2012Q3                               14.0                         3.0                                  NaN           NaN                   2.0                            139.0                   11.0                               74.0         17.0                            NaN                                      NaN           27.0                                            NaN                                     20.0                                            6.0                                               4.0                                 1.0                       NaN          34.0                           21.0                             2.0        NaN              6.0
2012Q4                               59.0                        15.0                                  NaN           NaN                   9.0                            725.0                   82.0                              533.0        113.0                            8.0                                      3.0          150.0                                            NaN                                    152.0                                           12.0                                              35.0                                10.0                       1.0         276.0                          177.0                            52.0        NaN             17.0
2013Q1                              162.0                        63.0                                  NaN           NaN                  40.0                           2170.0                  197.0                             1631.0        294.0                           28.0                                      6.0          334.0                                            NaN                                    536.0                                           46.0                                             109.0                                16.0                

In [21]:
Perf[Perf['Delinquency_Bucket']=='151+'].pivot_table(values='Unique_Order_ID',index = 'YQ',columns ='Industry',aggfunc='count')/Perf.pivot_table(values='Unique_Order_ID',index = 'YQ',columns ='Industry',aggfunc='count')

Industry  Accommodation and Food Services  Administrative and Support  Arts, Entertainment, and Recreation  Construction  Educational Services  Engineering  Federal Government/Associations  Finance and Insurance  Health Care and Social Assistance  Healthcare  Information  Local Government/Associations  Machinery  Management of Companies and Enterprises  Manufacturing  Mining, Quarrying, and Oil and Gas Extraction  Nursing and Residential Care Facilities  Other Services (except Public Administration)  Professional, Scientific, and Technical Services  Real Estate and Rental and Leasing  Retail & Wholesale Trade  Retail Trade  State Government/Associations  Transportation and Warehousing  Utilities  Wholesale Trade
YQ                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               
2012Q1                                NaN                         NaN                                  NaN           NaN                   NaN          NaN                              NaN                    NaN                                NaN         NaN          NaN                            NaN        NaN                                      NaN            NaN                                            NaN                                      NaN                                            NaN                                               NaN                                 NaN                       NaN           NaN                            NaN                             NaN        NaN              NaN
2012Q2                                NaN                         NaN                                  NaN           NaN                   NaN          NaN                              NaN                    NaN                                NaN         NaN          NaN                            NaN        NaN                                      NaN       0.000161                                            NaN                                      NaN                                            NaN                                               NaN                                 NaN                       NaN      0.000158                            NaN                             NaN        NaN              NaN
2012Q3                           0.003010                    0.002295                                  NaN           NaN              0.000870          NaN                         0.001843               0.002719                           0.001265         NaN     0.001974                            NaN        NaN                                      NaN       0.002446                                            NaN                                 0.001639                                       0.000919                                          0.002670                            0.006061                       NaN      0.001497                       0.000761                        0.000237        NaN         0.005226
2012Q4                           0.007723                    0.007029                                  NaN           NaN              0.002407          NaN                         0.006014               0.010627                           0.005599         NaN     0.005077                       0.001733        NaN                                 0.005703       0.007896                     

In [24]:
x = Perf[Perf['Delinquency_Bucket']=='151+'].pivot_table(values='Unique_Order_ID',index = 'YQ',columns ='Industry',aggfunc='count')/Perf.pivot_table(values='Unique_Order_ID',index = 'YQ',columns ='Industry',aggfunc='count')
x.to_csv('./data/Industry_DQ_rate.csv')

In [ ]:
def FPD(df,ID,balance_ind,period=1):
    df_sub = df.groupby(ID).head(period+1)
    df_sub['diff'] = df_sub[balance_ind].diff(-1*period)
    final = pd.DataFrame(df_sub.values[::period+1],index = df_sub.index[::period+1])
    final.columns = list(df_sub)
    return final



def check_FDP(df,FPD_df,balance_ind,file_name):
    df_1 = df.loc[df.groupby('Unique_Order_ID')['Year_and_Month'].idxmin()]
    df_sub = df_1.merge(FPD_df[['Unique_Order_ID','diff']],how = 'left', on= 'Unique_Order_ID')
    df_sub['FPD_flag'] = df_sub['diff'].apply(lambda x: 1 if x == 0 else 0)
    df_sub['FPD_Loss'] = df_sub['FPD_flag']*df_sub[balance_ind]
    df_sub['Year_and_Month'] = df_sub['Year_and_Month'].apply(lambda x: pd.to_datetime(str(x),format = '%Y%m'))
    df_sub.groupby('Year_and_Month').agg({'Unique_Order_ID':'count','FPD_flag':'sum',balance_ind:'sum','FPD_Loss':'sum'}).to_csv('./data/{}.csv'.format(file_name))

    return df_sub.groupby('Year_and_Month').agg({'Unique_Order_ID':'count','FPD_flag':'sum',balance_ind:'sum','FPD_Loss':'sum'}).reset_index()

In [ ]:
DQ151 = Perf[Perf['Delinquency_Bucket']=='151+']

In [30]:
# Perf[Perf['Delinquency_Bucket']=='151+']['Unique_Order_ID'].nunique()

365539

In [11]:
DQ151 = DQ151.merge(DQ151.groupby('Unique_Order_ID').size().reset_index(), how='left',on='Unique_Order_ID')

In [12]:
DQ151.rename(columns = {0:'duration'},inplace = True)

In [15]:
DQ151.head()

Unique_Order_ID  Unique_Customer_ID  Order_Amount Product_Markup Payments_Due  Current_Balance Date_account_went_delinquent Default_Status Delinquency_Bucket  Losses Auto_Pay_Enrollment Order_Closed_Flag Type_of_Backup_Payment Spending_Limit_at_time_of_Order Tenure_at_time_of_Order Salary_at_time_of_Order        Street1_x Street2_x     City_x State_x    Zip_x                                      items_ordered Year_and_Month   EMPSTATUS  Order_Date  Unique_Company_ID Enrollment_Date  Assigned_Spending_Limit  Customer_Tenure  Customer_Salary Prior_Customer_Flag        Street1_y Street2_y     City_y State_y  Zip_y      Status   Term_Date Active  Client ID            Account Name  Current Eligibles  Eligibles at time of Launch                           Industry  NAICS Code                    NAICS Description               Broker     TPA_x Launch Date Termination Date Affiliate/Fed Gov?                                Cash      YQ  duration
0        10003087           160793256       1405.15              .        54.04           216.16                   03/31/2015           151+               151+     0.0                  PD                 N                    ACH                            45.1                     162                37654.16   317 RUGGLES RD       NaN   FERGUSON      MO  63135.0  SquareTrade 2-Year Tablet Warranty Plus Accide...     2015-07-01  Terminated  03/15/2014             2250.0      02/25/2014                   4510.0            162.0         37654.16        Repeat Buyer   4094 Esseldale       NaN     St.Ann      MO  63074    Employed         NaN      Y     2250.0              DAVITA INC            43022.0                      27503.0  Health Care and Social Assistance    621492.0              Kidney Dialysis Centers       Beneplace, Inc  Paylogix  2011-01-03              NaT          Affiliate  TPA sends cash on behalf of client  2015Q3         3
1        10003087           160793256       1405.15              .        54.04           216.16                   03/31/2015           151+               151+     0.0                  PD                 N                    ACH                            45.1                     162                37654.16   317 RUGGLES RD       NaN   FERGUSON      MO  63135.0  SquareTrade 2-Year Tablet Warranty Plus Accide...     2015-08-01  Terminated  03/15/2014             2250.0      02/25/2014                   4510.0            162.0         37654.16        Repeat Buyer   4094 Esseldale       NaN     St.Ann      MO  63074    Employed         NaN      Y     2250.0              DAVITA INC            43022.0                      27503.0  Health Care and Social Assistance    621492.0              Kidney Dialysis Centers       Beneplace, Inc  Paylogix  2011-01-03              NaT          Affiliate  TPA sends cash on behalf of client  2015Q3         3
2        10003087           160793256       1405.15              .        54.04           216.16                   03/31/2015           151+               151+     0.0                  PD                 N                    ACH                            45.1                     162                37654.16   317 RUGGLES RD       NaN   FERGUSON      MO  63135.0  SquareTrade 2-Year Tablet Warranty Plus Accide...     2015-09-01  Terminated  03/15/2014             2250.0      02/25/2014                   4510.0            162.0         37654.16        Repeat Buyer   4094 Esseldale       NaN     St.Ann      MO  63074    Employed         NaN      Y     2250.0              DAVITA INC            43022.0                      27503.0  Health Care and Social Assistance    621492.0              Kidney Dialysis Centers       Beneplace, Inc  Paylogix  2011-01-03              NaT          Affiliate  TPA sends cash on behalf of client  2015Q3         3
3        10009030           250047209       1364.24              .        52.47           430.75                   11/30/2014           151+               151+     0.0                  PD       

In [16]:
EarlyDQ = DQ151.loc[DQ151.groupby('Unique_Order_ID')['Year_and_Month'].idxmin()][['Unique_Order_ID','Year_and_Month']]

In [17]:
EarlyDQ = EarlyDQ.merge(DQ151[['Unique_Order_ID','duration','Year_and_Month']], how='left',on=['Unique_Order_ID','Year_and_Month'])

In [18]:
EarlyDQ

Unique_Order_ID Year_and_Month  duration
0             10003087     2015-07-01         3
1             10009030     2015-04-01         2
2             10013115     2015-04-01         4
3             10015019     2015-05-01         1
4             10016456     2015-04-01         5
5             10017047     2014-10-01         3
6             10017119     2015-07-01         5
7             10017496     2014-12-01        16
8             10017587     2015-12-01        12
9             10022024     2015-11-01         2
10            10022024     2015-11-01         2
11            10022124     2014-10-01         2
12            10025013     2014-11-01         1
13            10025031     2015-06-01         3
14            10025082     2014-12-01         1
15            10025118     2014-12-01         2
16            10025225     2015-02-01         6
17            10025289     2015-04-01         4
18            10025415     2014-12-01         3
19            10026053     2015-02-01         1
20            10026172     2014-12-01         1
21            10026202     2015-03-01         1
22            10027054     2014-11-01        15
23            10029007     2014-12-01         1
24            10029157     2014-10-01         4
25            10029422     2015-02-01         1
26            10029428     2015-09-01         5
27            10036110     2014-11-01         1
28            10036376     2015-02-01         2
29            10039145     2015-07-01         6
30            10040232     2015-02-01         1
31            10041050     2014-12-01         2
32            10049155     2014-12-01         3
33            10049236     2014-11-01         1
34            10049334     2015-03-01         2
35            10049486     2014-09-01         5
36            10050108     2014-12-01         1
37            10050136     2014-11-01         5
38            10050273     2015-08-01         2
39            10050283     2015-03-01         1
40            10050417     2014-09-01         2
41            10050441     2014-11-01         1
42            10050614     2014-12-01         1
43            10050697     2014-11-01         3
44            10050756     2015-05-01         1
45            10051014     2015-01-01         2
46            10051122     2015-09-01         2
47            10051389     2015-01-01         1
48            10052547     2014-12-01        10
49            10052603     2015-06-01         2
50            10053139     2015-05-01         1
51            10055074     2014-10-01         3
52            10055083     2015-01-01         2
53            10058056     2015-01-01         5
54            10058161     2014-11-01         1
55            10058194     2014-12-01         2
56            10058202     2015-02-01         1
57            10058207     2015-08-01         1
58            10058210     2015-09-01         1
59            10058407     2015-04-01         3
60            10060256     2015-01-01         3
61            10060282     2015-08-01         3
62            10061071     2015-04-01         5
63            10061154     2014-12-01         3
64            10061205     2015-08-01         1
65            10061269     2015-07-01         5
66            10061468     2014-12-01         1
67            10061492     2014-10-01         1
68            10061504     2016-02-01         2
69            10061528     2014-10-01         4
70            10061579     2015-02-01        22
71            10062201     2015-01-01         1
72            10063033     2014-12-01         2
73            10063294     2015-01-01         2
74            10063471     2015-02-01         1
75            10063533     2015-02-01         1
76            10063546     2015-06-01         1
77            10063632     2015-01-01         2
78            10063686     2015-05-01         2
79            10063751     2014-11-01         2
80            10063789     2014-10-01         1
81            10063792     2015-08-01         5
82            10063892 

In [32]:
EarlyDQ.groupby('Year_and_Month').agg({'duration':'mean'}).to_csv('./data/DQ151_Duration.csv')

In [ ]:
# sub = Perf[Perf['Unique_Order_ID'].isin([EarlyDQ['Unique_Order_ID'].unique()])]

In [19]:
sub = Perf.loc[Perf.groupby('Unique_Order_ID')['Year_and_Month'].idxmax()][['Unique_Order_ID','Default_Status']]

In [20]:
sub.head()

Unique_Order_ID Default_Status
11        10000091        Current
23        10001064        Current
36        10003058        Current
49        10003059        Current
62        10003064        Current

In [21]:
EarlyDQ = EarlyDQ.merge(sub, how='left', on='Unique_Order_ID')

In [22]:
EarlyDQ.pivot_table(values = 'Unique_Order_ID',index = 'Year_and_Month',columns = 'Default_Status',aggfunc = 'count')

Default_Status  001-030  031-060  061-090  091-120  121-150    151+  Bankruptcy  Chargeoff  Current  Fraud
Year_and_Month                                                                                            
2012-06-01          NaN      NaN      NaN      NaN      NaN     NaN         NaN        3.0      NaN    NaN
2012-07-01          NaN      NaN      NaN      NaN      NaN     NaN         NaN       11.0      3.0    NaN
2012-08-01          NaN      NaN      NaN      NaN      NaN     NaN         NaN       93.0      6.0    NaN
2012-09-01          NaN      NaN      NaN      NaN      NaN     NaN         1.0      177.0     18.0    NaN
2012-10-01          NaN      NaN      NaN      NaN      NaN     NaN         2.0      251.0     23.0    1.0
2012-11-01          NaN      NaN      NaN      NaN      NaN     NaN         1.0      347.0     36.0    NaN
2012-12-01          NaN      NaN      NaN      NaN      NaN     NaN         3.0      470.0     35.0    NaN
2013-01-01          NaN      NaN      NaN      NaN      NaN     NaN         9.0      615.0     59.0    NaN
2013-02-01          NaN      NaN      NaN      NaN      NaN     NaN         3.0      684.0     70.0    NaN
2013-03-01          NaN      NaN      NaN      NaN      NaN     NaN         3.0      828.0    107.0    NaN
2013-04-01          NaN      NaN      NaN      NaN      NaN     NaN         5.0      867.0    116.0    NaN
2013-05-01          NaN      NaN      NaN      NaN      NaN     NaN         4.0      856.0    119.0    NaN
2013-06-01          NaN      NaN      NaN      NaN      NaN     NaN         3.0      997.0    117.0    2.0
2013-07-01          NaN      NaN      NaN      NaN      NaN     NaN         7.0     1609.0    214.0    5.0
2013-08-01          NaN      NaN      NaN      NaN      NaN     NaN         9.0     1678.0    195.0    1.0
2013-09-01          NaN      NaN      NaN      NaN      NaN     NaN         8.0     1661.0    204.0    NaN
2013-10-01          NaN      NaN      NaN      NaN      NaN     NaN         6.0     1950.0    244.0    1.0
2013-11-01          NaN      NaN      NaN      NaN      NaN     NaN         6.0     1884.0    305.0    NaN
2013-12-01          NaN      NaN      NaN      NaN      NaN     NaN        11.0     1959.0    637.0    2.0
2014-01-01          NaN      NaN      NaN      NaN      NaN     NaN         5.0     2283.0    406.0    1.0
2014-02-01          NaN      NaN      NaN      NaN      NaN     NaN        11.0     1432.0    282.0    NaN
2014-03-01          NaN      NaN      NaN      NaN      NaN     NaN        11.0     1842.0    323.0    NaN
2014-04-01          NaN      NaN      NaN      NaN      NaN     NaN        13.0     1634.0    376.0    NaN
2014-05-01          NaN      NaN      NaN      NaN      NaN     NaN         9.0     1338.0    358.0    NaN
2014-06-01          NaN      NaN      NaN      NaN      NaN     NaN         7.0     1259.0    346.0    NaN
2014-07-01          NaN      NaN      NaN      NaN      NaN     NaN        14.0     1880.0    258.0    3.0
2014-08-01          NaN      NaN      NaN      NaN      NaN     NaN        21.0     2250.0    231.0    NaN
2014-09-01          NaN      NaN      NaN      NaN      NaN     NaN        18.0     2119.0    223.0    2.0
2014-10-01          NaN      NaN      NaN      1.0      NaN     NaN        20.0     2168.0    239.0    1.0
2014-11-01          NaN      NaN      NaN      NaN      NaN     1.0        17.0     2077.0    242.0    NaN
2014-12-01          NaN      NaN      NaN      NaN      NaN     NaN        25.0     2721.0    288.0    3.0
2015-01-01          NaN      NaN      NaN      NaN      NaN     NaN        24.0     2475.0    321.0    4.0
2015-02-01          NaN      NaN      NaN      NaN      NaN     3.0        18.0     2199.0    286.0    NaN
2015-03-01          NaN      NaN      NaN      NaN      NaN     NaN        61.0     2459.0    247.0    2.0
2015-04-01          NaN      NaN      NaN      NaN      NaN     NaN        38.0     2082.0    273.0    4.0
2015-05-01          NaN      NaN      NaN

In [31]:
EarlyDQ.groupby('Year_and_Month').agg({'Unique_Order_ID':'count','duration':'mean'}).plt()

Unique_Order_ID  duration
Year_and_Month                           
2012-06-01                    3  2.666667
2012-07-01                   14  4.785714
2012-08-01                   99  5.909091
2012-09-01                  196  6.336735
2012-10-01                  277  6.191336
2012-11-01                  384  6.820312
2012-12-01                  508  6.818898
2013-01-01                  683  5.695461
2013-02-01                  757  5.046235
2013-03-01                  938  5.036247
2013-04-01                  988  4.251012
2013-05-01                  979  4.437181
2013-06-01                 1119  4.316354
2013-07-01                 1835  4.723161
2013-08-01                 1883  4.039830
2013-09-01                 1873  4.116391
2013-10-01                 2201  3.977737
2013-11-01                 2195  4.279271
2013-12-01                 2609  4.014948
2014-01-01                 2695  3.973655
2014-02-01                 1725  4.175072
2014-03-01                 2176  3.752757
2014-04-01                 2023  3.684132
2014-05-01                 1705  3.874487
2014-06-01                 1612  4.272953
2014-07-01                 2155  3.771694
2014-08-01                 2502  3.313749
2014-09-01                 2362  3.373412
2014-10-01                 2429  3.355290
2014-11-01                 2337  3.634574
2014-12-01                 3037  3.521238
2015-01-01                 2824  3.483003
2015-02-01                 2506  3.329609
2015-03-01                 2769  3.455038
2015-04-01                 2397  3.443054
2015-05-01                 2233  3.629198
2015-06-01                 2382  4.141058
2015-07-01                 2776  3.888329
2015-08-01                 2964  3.952429
2015-09-01                 3041  3.742190
2015-10-01                 2851  4.417397
2015-11-01                 3298  4.571862
2015-12-01                 3857  4.852476
2016-01-01                 4050  4.900247
2016-02-01                 3584  4.533482
2016-03-01                 3890  4.151928
2016-04-01                 3661  3.805244
2016-05-01                 3334  3.976305
2016-06-01                 3159  4.342513
2016-07-01                 3671  4.254699
2016-08-01                 4274  4.178053
2016-09-01                 4320  4.137037
2016-10-01                 4584  4.242801
2016-11-01                 5291  4.464562
2016-12-01                 4866  4.031443
2017-01-01                 5191  4.830668
2017-02-01                 4796  5.676814
2017-03-01                 4806  6.501873
2017-04-01                 4979  6.588271
2017-05-01                 5093  5.743570
2017-06-01                 4052  4.369694
2017-07-01                 5153  4.324083
2017-08-01                 5509  4.252859
2017-09-01                 5958  4.257133
2017-10-01                 6379  4.591942
2017-11-01                 5770  5.168458
2017-12-01                 6652  5.290890
2018-01-01                 6360  5.494811
2018-02-01                 5806  5.218739
2018-03-01                 6331  4.791186
2018-04-01                 6020  4.783721
2018-05-01                 5745  4.720279
2018-06-01                 5282  4.860470
2018-07-01                 6669  4.814515
2018-08-01                 7167  4.680340
2018-09-01                 7539  4.411593
2018-10-01                 8777  4.561354
2018-11-01                 8094  4.276748
2018-12-01                 9191  4.363181
2019-01-01                 9585  4.061450
2019-02-01                 8809  3.867862
2019-03-01                 9381  3.706428
2019-04-01                 9204  4.312364
2019-05-01                 8351  4.999761
2019-06-01                 8575  4.483732
2019-07-01                10017  3.703304
2019-08-01                 9572  2.734016
2019-09-01                 8012  1.962307
2019-10-01                 8887  1.009002

In [ ]:
DQ151.groupby('Year_and_Month')['Unique_Order_ID'].size()

In [ ]:
EarlyDQ.groupby('Year_and_Month').agg({'Unique_Order_ID':'count','duration':'mean'}).plt('Unique_Order_ID')

In [40]:
Perf.pivot_table(values = 'Unique_Order_ID',index = 'YQ',columns = 'Default_Status',aggfunc='count',margins = True).to_csv('Default_DQ.csv')

In [ ]:
EarlyDQ.pivot_table(values = 'Unique_Order_ID',index = 'Year_and_Month',columns = 'Default_Status',aggfunc = 'count')

In [13]:
DQ151_perf = Perf[Perf['Unique_Order_ID'].isin(DQ151['Unique_Order_ID'].unique())]

In [24]:
DQ151_perf.shape

(6080973, 53)

In [25]:
len(DQ151['Unique_Order_ID'].unique())

365539

In [26]:
len(DQ151_perf['Unique_Order_ID'].unique())

365539

In [15]:
# DQ151_perf.to_csv('./data/DQ151_perf.csv',index = False)   

## 12.06 Vintage view of DQ151+ and C/O 

In [16]:
Perf.groupby(['Default_Status','Delinquency_Bucket']).size()

Default_Status  Delinquency_Bucket
001-030         001-030                2977970
031-060         031-060                 823220
061-090         061-090                 586676
091-120         091-120                 483602
121-150         121-150                 427299
151+            151+                   1441095
Bankruptcy      000-000                  44018
                001-030                  10003
                031-060                  10817
                061-090                  11573
                091-120                  12041
                121-150                  12468
                151+                    106182
Chargeoff       000-000                 347866
                001-030                    259
                031-060                    342
                061-090                    420
                091-120                    468
                121-150                    491
                151+                      1954
Current         000-000  

In [10]:
# Subgroup performance data after 2015
Perf_af15 = Perf[Perf['YQ']>='2015Q1']

In [11]:
YQ_list = Perf_af15['YQ'].unique()
YQ_list

<PeriodArray>
['2015Q1', '2015Q2', '2015Q3', '2015Q4', '2016Q1', '2016Q2', '2016Q3', '2016Q4', '2017Q1', '2017Q2', '2017Q3', '2017Q4', '2018Q1', '2018Q2', '2018Q3', '2018Q4', '2019Q1', '2019Q2', '2019Q3', '2019Q4']
Length: 20, dtype: period[Q-DEC]

In [12]:
Q1_15_Order = Perf_af15[Perf_af15['YQ']=='2015Q1'].loc[Perf_af15[Perf_af15['YQ']=='2015Q1'].groupby('Unique_Order_ID')['Year_and_Month'].idxmin()]['Unique_Order_ID'].tolist()

In [23]:
x = Perf.loc[Perf.groupby('Unique_Order_ID')['Year_and_Month'].idxmin()]
x[x['Year_and_Month']=='2015Q1']

Unique_Order_ID  Unique_Customer_ID Order_Amount Product_Markup Payments_Due  Current_Balance Date_account_went_delinquent Default_Status Delinquency_Bucket  Losses Auto_Pay_Enrollment Order_Closed_Flag Type_of_Backup_Payment Spending_Limit_at_time_of_Order Tenure_at_time_of_Order Salary_at_time_of_Order                    Street1_x          Street2_x              City_x State_x    Zip_x                                      items_ordered Year_and_Month   EMPSTATUS  Order_Date  Unique_Company_ID Enrollment_Date  Assigned_Spending_Limit  Customer_Tenure  Customer_Salary Prior_Customer_Flag                                Street1_y                  Street2_y              City_y State_y  Zip_y       Status   Term_Date      Active  Client ID                                       Account Name  Current Eligibles  Eligibles at time of Launch                                          Industry  NAICS Code                                  NAICS Description  \
2294677        11210928           248076439       594.71              .        22.75           500.50                   01/31/2016        Current            000-000     0.0                  PD                 N                    ACH                           17.35                     100                  249.60             335 DRAKE ELM DR                NaN           KISSIMMEE      FL  34743.0  SquareTrade 5-Year TV Warranty; Vizio 32 Class...     2015-01-01    Employed  12/01/2014             2366.0      02/25/2014                   1735.0            100.0     24960.000000        Repeat Buyer                         335 DRAKE ELM DR                        NaN           KISSIMMEE      FL  34743   Terminated  12/01/2015           Y     2366.0                      DIAMOND RESORTS INTERNATIONAL             4252.0                       2321.0                   Accommodation and Food Services    721110.0           Hotels (except Casino Hotels) and Motels   
2296586        11211341           100579167       2141.2              .        82.35          1449.46                            .        Current            000-000     0.0                  PA                 N                    ACH                              42                     139                38357.28            65 QUARRY HILL RD                NaN            NEWVILLE      PA  17241.0            Sears Automotive Center Gift Card $2000     2015-01-01    Employed  11/24/2014             2049.0      02/24/2014                   4200.0            139.0     38357.280000        Repeat Buyer                        65 QUARRY HILL RD                        NaN            NEWVILLE      PA  17241     Employed         NaN           Y     2049.0  FEDERAL GOVERNMENT/POSTAL WORKERS/NIH/DEPT OF ...                NaN                    2900000.0                   Federal Government/Associations         NaN                                                NaN   
2302956        11212728           300475265      1405.69              .        54.06          1189.32                   04/30/2015        Current            000-000     0.0                  PA                 N                    ACH                            30.6                      83                31740.80           114 scenic view dr                NaN           swannanoa      NC  28778.0  SquareTrade 5-Year TV Warranty; Vizio 55 Class...     2015-01-01    Employed  11/25/2014             2049.0      11/25/2014                   3060.0             83.0     31740.800000        Repeat Buyer                       114 scenic view dr                        NaN           swannanoa      NC  28778     Employed         NaN           Y     2049.0  FEDERAL GOVERNMENT/POSTAL WORKERS/NIH/DEPT OF ...                NaN                    2900000.0                   Federal Government/Associations         NaN                                                NaN   
2321742        11216880           193772690      1184.79              .        45.56          1047.88                            .  

In [36]:
len(x[x['YQ']=='2015Q1']['Unique_Order_ID'].unique())

52512

In [41]:
x.groupby('YQ')['Unique_Order_ID'].size()

YQ
2012Q1     26485
2012Q2     31439
2012Q3     40828
2012Q4     82961
2013Q1     39948
2013Q2     42595
2013Q3     45832
2013Q4     99833
2014Q1     42396
2014Q2     50516
2014Q3     58077
2014Q4    126607
2015Q1     52512
2015Q2     62986
2015Q3     79519
2015Q4    171290
2016Q1     75745
2016Q2     86036
2016Q3     96710
2016Q4    198514
2017Q1     90658
2017Q2    105131
2017Q3    112373
2017Q4    231694
2018Q1    118285
2018Q2    141890
2018Q3    145098
2018Q4    274737
2019Q1    120534
2019Q2    144499
2019Q3    148685
2019Q4     54280
Freq: Q-DEC, Name: Unique_Order_ID, dtype: int64

In [26]:
len(Q1_15_Order)

351411

In [37]:
Q1_15 = Perf_af15[Perf_af15['Unique_Order_ID'].isin(x[x['YQ']=='2015Q1']['Unique_Order_ID'].unique())]

In [38]:
y = Q1_15[Q1_15.Default_Status.isin(['151+','Chargeoff'])].pivot_table(values = 'Unique_Order_ID',index = 'Year_and_Month',columns = 'Default_Status',aggfunc='count')/18045

In [39]:
y['C'] = np.arange(1+,len(y)+1)

In [40]:
y

Default_Status      151+  Chargeoff   C
Year_and_Month                         
2015-06-01      0.000222        NaN   1
2015-07-01      0.005154   0.000222   2
2015-08-01      0.021945   0.003103   3
2015-09-01      0.048324   0.010695   4
2015-10-01      0.071543   0.017290   5
2015-11-01      0.086561   0.025159   6
2015-12-01      0.103796   0.015683   7
2016-01-01      0.125298   0.036686   8
2016-02-01      0.133832   0.038903   9
2016-03-01      0.135550   0.052424  10
2016-04-01      0.136270   0.058410  11
2016-05-01      0.125242   0.036908  12
2016-06-01      0.101912   0.048656  13
2016-07-01      0.092103   0.028318  14
2016-08-01      0.088002   0.012025  15
2016-09-01      0.076032   0.011083  16
2016-10-01      0.052424   0.017733  17
2016-11-01      0.036298   0.013799  18
2016-12-01      0.029426   0.004821  19
2017-01-01      0.024716   0.003547  20
2017-02-01      0.017678   0.005098  21
2017-03-01      0.013466   0.002494  22
2017-04-01      0.011305   0.001108  23
2017-05-01      0.008867   0.001441  24
2017-06-01      0.006761   0.001441  25
2017-07-01      0.005763   0.000831  26
2017-08-01      0.004323   0.001219  27
2017-09-01      0.003547   0.000665  28
2017-10-01      0.003491   0.000277  29
2017-11-01      0.003214   0.000222  30
2017-12-01      0.003325   0.000222  31
2018-01-01      0.002937   0.000443  32
2018-02-01      0.002328   0.000388  33
2018-03-01      0.001385   0.001053  34
2018-04-01      0.001330   0.000222  35
2018-05-01      0.001219   0.000277  36
2018-06-01      0.001219   0.000222  37
2018-07-01      0.001108   0.000277  38
2018-08-01      0.001108   0.000222  39
2018-09-01      0.001108   0.000277  40
2018-10-01      0.000998   0.000333  41
2018-11-01      0.000887   0.000277  42
2018-12-01      0.000887   0.000222  43
2019-01-01      0.000887   0.000222  44
2019-02-01      0.000554   0.000554  45
2019-03-01      0.000443   0.000277  46
2019-04-01      0.000388   0.000277  47
2019-05-01      0.000388   0.000222  48
2019-06-01      0.000388   0.000222  49
2019-07-01      0.000277   0.000333  50
2019-08-01      0.000277   0.000222  51
2019-09-01      0.000277   0.000222  52
2019-10-01      0.000222   0.000277  53

In [31]:
np.arange(1,len(y))

array([ 1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15, 16, 17,
       18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34,
       35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51,
       52])

In [31]:
Q1_15.Default_Status.unique()

array(['Current', '001-030', '031-060', '061-090', '091-120', '121-150',
       '151+', 'Chargeoff', 'Fraud', 'Bankruptcy'], dtype=object)

In [ ]:
x = Perf.loc[Perf.groupby('Unique_Order_ID')['Year_and_Month'].idxmin()]

In [70]:
x.head()

Unique_Order_ID  Unique_Customer_ID Order_Amount Product_Markup Payments_Due  Current_Balance Date_account_went_delinquent Default_Status Delinquency_Bucket  Losses Auto_Pay_Enrollment Order_Closed_Flag Type_of_Backup_Payment Spending_Limit_at_time_of_Order Tenure_at_time_of_Order Salary_at_time_of_Order          Street1_x Street2_x        City_x State_x    Zip_x                                      items_ordered Year_and_Month EMPSTATUS  Order_Date  Unique_Company_ID Enrollment_Date  Assigned_Spending_Limit  Customer_Tenure  Customer_Salary Prior_Customer_Flag               Street1_y Street2_y        City_y State_y  Zip_y       Status   Term_Date      Active  Client ID                                       Account Name  Current Eligibles  Eligibles at time of Launch                           Industry  NAICS Code                        NAICS Description                         Broker TPA_x Launch Date Termination Date Affiliate/Fed Gov? Cash      YQ
0         10000091           100486182      1072.88              .        40.11           907.86                            .        Current            000-000     0.0                  PA                 N                    ACH                            96.6                     327                  800.29    929 IMPERIAL CT       NaN    HALETHORPE      MD  21227.0  DeWalt 12in 15-Amp Double-Bevel Compound Miter...     2014-04-01  Employed  03/15/2014             2049.0      02/25/2014                   9660.0            327.0         80029.00        Repeat Buyer         929 IMPERIAL CT       NaN    HALETHORPE      MD  21227     Employed         NaN           Y     2049.0  FEDERAL GOVERNMENT/POSTAL WORKERS/NIH/DEPT OF ...                NaN                    2900000.0    Federal Government/Associations         NaN                                      NaN                            NaN   NaN  2002-07-01              NaT            Fed Gov  NaN  2014Q2
12        10001064           211053736      1186.67              .        45.64          1095.36                            .        Current            000-000     0.0                  PD                 N                    ACH                           31.85                     169                31495.41    479 DEWDROP CIR     APT A    CINCINNATI      OH  45240.0  Beautyrest Recharge Laingsburg Queen Plush Mat...     2014-04-01  Employed  03/15/2014             2311.0      02/25/2014                   3185.0            169.0         31495.41        Repeat Buyer         479 DEWDROP CIR     APT A    CINCINNATI      OH  45240   Terminated  09/17/2015  Terminated     2311.0                             CHARTER COMMUNICATIONS            70231.0                      42178.0                        Information    515210.0  Cable and Other Subscription Programing                            NaN   NaN  2012-09-01       2018-12-31          Affiliate  NaN  2014Q2
24        10003058           100230472       401.25              .        15.43           401.18                   06/30/2014        Current            000-000     0.0                  PD                 N                    ACH                            53.6                     108                39999.99   210 E GIRARD AVE       NaN     CEDARTOWN      GA  30125.0  Hoover MaxExtract 77 Multi Surface Pro Steam C...     2014-03-01  Employed  03/15/2014             2194.0      03/12/2014                   5360.0            108.0         39999.99        Repeat Buyer  2788 SCARLETT OHARA CT       NaN  DOUGLASVILLE      GA  30135     Employed         NaN           Y     2194.0                             WELLSTAR HEALTH SYSTEM            17192.0                       8224.0  Health Care and Social Assistance    622110.0   General Medical and Surgical Hospitals          Galloway & Associates   NaN  2008-10-14              NaT          Affiliate  NaN  2014Q1
37        10003059           245451072       937.53              .        36.06           901.25                            .        Cu

In [94]:
YQ_list[1].month

6

In [88]:
np.datetime64(YQ_list[1])

numpy.datetime64('2015-06-30')

In [130]:
def vintage_view(df, YQ, vintage):
    order_list = vintage[vintage['YQ'] == YQ]['Unique_Order_ID'].unique()
    df_YQ = df[df['Unique_Order_ID'].isin(order_list)]
    df_DQ = df_YQ[df_YQ.Default_Status.isin(['151+', 'Chargeoff'])]
    df_DQ = df_DQ.loc[df_DQ.groupby('Unique_Order_ID')[
        'Year_and_Month'].idxmin()]
    view = df_DQ.groupby('Year_and_Month')[
        'Unique_Order_ID'].size().reset_index()
    view['count'] = view['Unique_Order_ID'].cumsum()
    view['DQ_Rate'] = view['count']/len(order_list)
#     view = (df_YQ[df_YQ.Default_Status.isin(['151+','Chargeoff'])].pivot_table(values = 'Unique_Order_ID',index = 'Year_and_Month',columns = 'Default_Status',aggfunc='count')/len(order_list)).rename_axis(None, axis=1).reset_index()
    view['month_order'] = np.arange(1+round((view['Year_and_Month'].min()-df_YQ['Year_and_Month'].min())/np.timedelta64(1, 'M')), len(
        view)+1+round((view['Year_and_Month'].min()-df_YQ['Year_and_Month'].min())/np.timedelta64(1, 'M')))
    return view

In [13]:
Perf = pd.read_csv(path+'Performance_Data_Request_20191204.csv',nrows = 10000)

In [12]:
path = '/Users/XSun37/Desktop/Power Purchasing/purchasingpowerdocuments/'

In [16]:
Perf['Year_and_Month'].min().month

3

In [120]:
YQ_list[3].month

12

In [ ]:
# def vintage_view_loss(df, YQ, vintage ):
#     order_list = vintage[vintage['YQ']==YQ]['Unique_Order_ID'].unique()
#     df_YQ = df[df['Unique_Order_ID'].isin(order_list)]
#     view = (df_YQ[df_YQ.Default_Status.isin(['151+','Chargeoff'])].pivot_table(values = 'Current_Balance',index = 'Year_and_Month',columns = 'Default_Status',aggfunc='sum')/len(order_list)).rename_axis(None, axis=1).reset_index()
#     view['month_order'] = np.arange(1+round((view['Year_and_Month'].min()-np.datetime64('{}-0{}-01'.format(YQ.year,YQ.month-2)))/np.timedelta64(1, 'M')),len(view)+1+round((view['Year_and_Month'].min()-np.datetime64('{}-0{}-01'.format(YQ.year,YQ.month-2)))/np.timedelta64(1, 'M')))
#     return view

In [101]:
len(YQ_list)

20

In [102]:
YQ_list[4]

Period('2016Q1', 'Q-DEC')

In [144]:
# Q1
temp = pd.DataFrame(np.arange(1,31),columns = ['month_order'])
Q1_vintage_list = [temp]
for i in range(int(len(YQ_list)/4)):
    print(YQ_list[i*4])
    view = vintage_view(Perf, YQ_list[i*4], x)
#     view['Vintage'] = str(YQ_list[i*4])
    view.rename(columns = {'151+':str(YQ_list[i*4]) + ' 151+','Chargeoff':str(YQ_list[i*4]) + ' Chargeoff'},inplace = True)
#     view.columns = [str(YQ_list[i*4]) + ' ' + str(col)  for col in view.columns]
    Q1_vintage_list.append(view)

2015Q1
2016Q1
2017Q1
2018Q1
2019Q1


In [114]:
# Q2
Q2_vintage_list = []
for i in range(int(len(YQ_list)/4)):
    print(YQ_list[1+i*4])
    view = vintage_view(Perf, YQ_list[1+i*4], x)
    Q2_vintage_list.append(view)

2015Q2
2016Q2
2017Q2
2018Q2
2019Q2


In [115]:
# Q3
Q3_vintage_list = []
for i in range(int(len(YQ_list)/4)):
    print(YQ_list[2+i*4])
    view = vintage_view(Perf, YQ_list[2+i*4], x)
    Q3_vintage_list.append(view)

2015Q3
2016Q3
2017Q3
2018Q3
2019Q3


In [128]:
# Q4
Q4_vintage_list = []
for i in range(int(len(YQ_list)/4)-1):
    print(YQ_list[3+i*4])
    view = vintage_view(Perf, YQ_list[3+i*4], x)
    Q4_vintage_list.append(view)

2015Q4
2016Q4
2017Q4
2018Q4


In [145]:
Q1_vintage_list[0]

month_order
0             0
1             1
2             2
3             3
4             4
5             5
6             6
7             7
8             8
9             9
10           10
11           11
12           12
13           13
14           14
15           15
16           16
17           17
18           18
19           19
20           20
21           21
22           22
23           23
24           24
25           25
26           26
27           27
28           28
29           29
30           30

In [139]:
temp = pd.DataFrame(np.arange(1,31),columns = ['month_order'])

In [148]:
from functools import reduce

In [149]:
Q1_final=reduce(lambda x,y: pd.merge(x,y.iloc[:,1:], how='left',on='month_order'),Q1_vintage_list)

In [151]:
Q1_final.to_csv('./data/Q1.csv',index = False)

In [152]:
Q1_final

month_order  2015Q1 151+  2015Q1 Chargeoff  2016Q1 151+  2016Q1 Chargeoff  2017Q1 151+  2017Q1 Chargeoff  2018Q1 151+  2018Q1 Chargeoff  2019Q1 151+  2019Q1 Chargeoff
0             0          NaN               NaN          NaN               NaN          NaN               NaN          NaN               NaN          NaN               NaN
1             1          NaN               NaN          NaN               NaN          NaN               NaN     0.000068               NaN          NaN               NaN
2             2          NaN               NaN          NaN               NaN          NaN          0.000011     0.000101               NaN          NaN               NaN
3             3          NaN               NaN     0.000013          0.000013     0.000188               NaN     0.000085          0.000017          NaN               NaN
4             4          NaN               NaN     0.000013          0.000013     0.001997               NaN     0.000076               NaN          NaN               NaN
5             5          NaN               NaN          NaN          0.000013     0.009453          0.000463     0.000076               NaN          NaN               NaN
6             6     0.000076               NaN     0.000053          0.000013     0.021223          0.002824     0.000178          0.000034     0.000141          0.000008
7             7     0.001771          0.000076     0.001690          0.000449     0.032705          0.007401     0.002367          0.000085     0.002970          0.000124
8             8     0.007541          0.001066     0.008278          0.000937     0.037691          0.015652     0.010449          0.000076     0.012818          0.000050
9             9     0.016606          0.003675     0.017915          0.004145     0.044541          0.021498     0.025388          0.000228     0.025553          0.005135
10           10     0.024585          0.005941     0.028662          0.006443     0.048953          0.027918     0.043201          0.001065     0.042469          0.001634
11           11     0.029746          0.008646     0.036266          0.010179     0.053233          0.020748     0.050108          0.009891          NaN               NaN
12           12     0.035668          0.005389     0.039131          0.015816     0.064484          0.005504     0.058841          0.007321          NaN               NaN
13           13     0.043057          0.012607     0.045376          0.014813     0.060381          0.015674     0.072418          0.002917          NaN               NaN
14           14     0.045989          0.013368     0.041151          0.019143     0.066812          0.005603     0.065097          0.020763          NaN               NaN
15           15     0.046580          0.018015     0.037560          0.020279     0.053818          0.023396     0.061859          0.015657          NaN               NaN
16           16     0.046827          0.020072     0.041587          0.006733     0.048920          0.015233     0.056102          0.017449          NaN               NaN
17           17     0.043038          0.012683     0.047383          0.004964     0.042886          0.013402     0.052120          0.014651          NaN               NaN
18           18     0.035021          0.016720     0.047871          0.007512     0.033367          0.013777     0.042465          0.019233          NaN               NaN
19           19     0.031650          0.009731     0.045059          0.008463     0.025304          0.011990     0.039143          0.009824          NaN               NaN
20           20     0.030241          0.004132     0.035514          0.012304     0.014042          0.014295     0.040707          0.000989          NaN               NaN
21           21     0.026127          0.003809     0.029058          0.007208     0.012178          0.002901     0.037486          0.003094          NaN               NaN
22           22     0.018015          0.006094     0.023883          0.

In [141]:
temp.merge(Q1_vintage_list[0].iloc[:,1:],how = 'left', on = 'month_order')

month_order  151+2015Q1  Chargeoff2015Q1  month_order2015Q1
0             0         NaN              NaN                NaN
1             1         NaN              NaN                NaN
2             2         NaN              NaN                NaN
3             3         NaN              NaN                NaN
4             4         NaN              NaN                NaN
5             5         NaN              NaN                NaN
6             6    0.000076              NaN                6.0
7             7    0.001771         0.000076                7.0
8             8    0.007541         0.001066                8.0
9             9    0.016606         0.003675                9.0
10           10    0.024585         0.005941               10.0
11           11    0.029746         0.008646               11.0
12           12    0.035668         0.005389               12.0
13           13    0.043057         0.012607               13.0
14           14    0.045989         0.013368               14.0
15           15    0.046580         0.018015               15.0
16           16    0.046827         0.020072               16.0
17           17    0.043038         0.012683               17.0
18           18    0.035021         0.016720               18.0
19           19    0.031650         0.009731               19.0
20           20    0.030241         0.004132               20.0
21           21    0.026127         0.003809               21.0
22           22    0.018015         0.006094               22.0
23           23    0.012473         0.004742               23.0
24           24    0.010112         0.001657               24.0
25           25    0.008493         0.001219               25.0
26           26    0.006075         0.001752               26.0
27           27    0.004628         0.000857               27.0
28           28    0.003885         0.000381               28.0
29           29    0.003047         0.000495               29.0
30           30    0.002323         0.000495               30.0

In [134]:
Q1_vintage_list[1]

Year_and_Month      151+  Chargeoff  month_order Vintage
0      2016-03-01  0.000013   0.000013            3  2016Q1
1      2016-04-01  0.000013   0.000013            4  2016Q1
2      2016-05-01       NaN   0.000013            5  2016Q1
3      2016-06-01  0.000053   0.000013            6  2016Q1
4      2016-07-01  0.001690   0.000449            7  2016Q1
5      2016-08-01  0.008278   0.000937            8  2016Q1
6      2016-09-01  0.017915   0.004145            9  2016Q1
7      2016-10-01  0.028662   0.006443           10  2016Q1
8      2016-11-01  0.036266   0.010179           11  2016Q1
9      2016-12-01  0.039131   0.015816           12  2016Q1
10     2017-01-01  0.045376   0.014813           13  2016Q1
11     2017-02-01  0.041151   0.019143           14  2016Q1
12     2017-03-01  0.037560   0.020279           15  2016Q1
13     2017-04-01  0.041587   0.006733           16  2016Q1
14     2017-05-01  0.047383   0.004964           17  2016Q1
15     2017-06-01  0.047871   0.007512           18  2016Q1
16     2017-07-01  0.045059   0.008463           19  2016Q1
17     2017-08-01  0.035514   0.012304           20  2016Q1
18     2017-09-01  0.029058   0.007208           21  2016Q1
19     2017-10-01  0.023883   0.004462           22  2016Q1
20     2017-11-01  0.019618   0.003380           23  2016Q1
21     2017-12-01  0.018179   0.001597           24  2016Q1
22     2018-01-01  0.016714   0.001518           25  2016Q1
23     2018-02-01  0.015671   0.000766           26  2016Q1
24     2018-03-01  0.004740   0.010707           27  2016Q1
25     2018-04-01  0.003670   0.000990           28  2016Q1
26     2018-05-01  0.003248   0.000449           29  2016Q1
27     2018-06-01  0.002456   0.000898           30  2016Q1
28     2018-07-01  0.001928   0.000594           31  2016Q1
29     2018-08-01  0.001729   0.000356           32  2016Q1
30     2018-09-01  0.001571   0.000290           33  2016Q1
31     2018-10-01  0.001347   0.000277           34  2016Q1
32     2018-11-01  0.001241   0.000172           35  2016Q1
33     2018-12-01  0.001122   0.000224           36  2016Q1
34     2019-01-01  0.001109   0.000158           37  2016Q1
35     2019-02-01  0.000766   0.000462           38  2016Q1
36     2019-03-01  0.000594   0.000317           39  2016Q1
37     2019-04-01  0.000528   0.000211           40  2016Q1
38     2019-05-01  0.000475   0.000185           41  2016Q1
39     2019-06-01  0.000436   0.000172           42  2016Q1
40     2019-07-01  0.000436   0.000145           43  2016Q1
41     2019-08-01  0.000422   0.000145           44  2016Q1
42     2019-09-01  0.000396   0.000158           45  2016Q1
43     2019-10-01  0.000330   0.000211           46  2016Q1

In [50]:
from datetime import datetime, timedelta

In [ ]:
closed = Perf[Perf['Order_Closed_Flag']=='Y']['Unique_Order_ID'].unique()

In [ ]:
DQ151[DQ151['Unique_Order_ID'].isin([closed])].groupby(['YQ'])['Unique_Order_ID'].size()

In [ ]:
DQ151[~DQ151['Unique_Order_ID'].isin([closed])].groupby(['YQ'])['Unique_Order_ID'].size()